# Google Drive

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Weights and Biases

This keeps track of training and validation loss while the model is being fitted. Run the cell below to install WandB.

In [ ]:
%%capture
!pip install wandb
!wandb login

# Imports

In [2]:
import torch
import torchvision
import torchvision.transforms as transforms
from torchvision.ops import sigmoid_focal_loss
import torch.nn.functional as F
from torch import nn
from torch.utils.data import Dataset, DataLoader, Sampler, RandomSampler, SubsetRandomSampler, random_split

import os
import random
import pandas as pd
import numpy as np
import pickle
#import wandb
from collections import defaultdict
from sklearn.metrics import matthews_corrcoef as mcc
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
import matplotlib.pyplot as plt

# Random Seed and Batch Size

In [3]:
# Set random seed and batch size for all random processes and datasets. Seed for saved datasets is 100.

seed = 100
batch_size = 64

# Data and Languages

In [4]:
data_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Datasets'

languages = [('cs', 'Czech'), ('nl', 'Dutch'), ('en', 'English'), ('fr', 'French'),
             ('de', 'German'), ('el', 'Greek'), ('it', 'Italian'), ('ko', 'Korean'),
             ('no', 'Norwegian'), ('es', 'Spanish'), ('sv', 'Swedish'), ('tr', 'Turkish')]

germanic = [('nl', 'Dutch'), ('en', 'English'), ('de', 'German')]
romantic = [('fr', 'French'), ('it', 'Italian'), ('es', 'Spanish')]
nordic = [('no', 'Norwegian'), ('sv', 'Swedish')]

families = [('Germanic', germanic), ('Romantic', romantic), ('Nordic', nordic)]

# Batch Sampler

**Note:** To get deterministic behavior from the EqualLengthsBatchSampler, you need to initialize it with a seed each time you initialize the corresponding DataLoader. If you initialize a new DataLoader without re-initializing the Sampler, it will not reset the RNG within the sampler and so you will get new samples for the new DataLoader. Example code is show below:

```
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)
fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce')

```
Each of the 10 epochs will give uniquely shuffled batches, but if you run the code block again it will give you the same 10 batches as the first time you ran it. If you don't want this behavior, feed in `seed=None`.

In [5]:
# Code copied (with edits and additional functions) from
# https://discuss.pytorch.org/t/tensorflow-esque-bucket-by-sequence-length/41284/27

class EqualLengthsBatchSampler(Sampler):

    def __init__(self, dataset, batch_size, seed):

        # Set random seed
        self.rng = np.random.default_rng(seed)

        # Remember batch size and number of samples
        self.batch_size = batch_size

        self.unique_lengths = set()
        self.samples = defaultdict(list)

        for i in range(0, len(dataset)):
            len_input = len(dataset[i][0])

            # Add length to set of all seen lengths
            self.unique_lengths.add(len_input)

            # For each length, keep track of which sample indices for this length
            # E.g.: self.lengths_to_sample = { 4: [3,5,11], 5: [1,2,9], ...}
            self.samples[len_input].append(i)

        # Delete lengths and corresponding samples if there are fewer than batch_size // 2
        # samples of that length.
        self.small_samples = set()
        for length in self.unique_lengths:
            if len(self.samples[length]) < batch_size // 2:
                self.small_samples.add(length)

        self.unique_lengths = self.unique_lengths - self.small_samples

        # Convert set of unique lengths to a list so we can shuffle it later
        self.unique_lengths = list(self.unique_lengths)

    def __len__(self):
        batches = 0
        for length in self.unique_lengths:
          batches += np.ceil(len(self.samples[length]) / self.batch_size).astype(int)
        return batches

    def __iter__(self):

        # Make list to store all batches of any length
        all_batches = []

        # Shuffle list of unique length pairs
        self.rng.shuffle(self.unique_lengths)

        # Iterate over all possible word lengths
        for length in self.unique_lengths:

            # Get indices of all samples for the current lengths
            # for example, all indices with a length of 8
            sequence_indices = self.samples[length]
            sequence_indices = np.array(sequence_indices)

            # Shuffle array of sequence indices
            self.rng.shuffle(sequence_indices)

            # Compute the number of batches
            num_batches = np.ceil(len(sequence_indices) / self.batch_size)

            # Loop over all possible batches of given length and add to list of all batches
            all_batches += [batch_indices for batch_indices in np.array_split(sequence_indices, num_batches)]

        # Shuffle list of all batches; this shuffles the order of batches but keeps their internal structure the same
        self.rng.shuffle(all_batches)
        for batch in all_batches:
          yield(np.asarray(batch))


    def show_batches(self):
      '''
      Print the different possible word lengths, the number of samples with each word length,
      the number of batches of size self.batch_size that can be made out of those samples,
      and the remainder, i.e. the number of samples in the final, smallest batch.
      (Note: if remainder is 0, that means the number of samples falls perfectly in n batches.)
      '''
      print(f'Length    # Samples    # Batches    Avg Batch Size')
      for length in self.unique_lengths:
          num_samples = len(self.samples[length])
          num_batches = np.ceil(num_samples / self.batch_size)
          average = num_samples / num_batches
          print(f'{length:>6} {num_samples:>12} {num_batches:>12.0f} {average:>12.1f}')

    def dropped_samples(self):
      '''
      Return dictionary of all words dropped from dataset for having too few samples of that length.
      '''
      small_samples = {}
      for length in self.small_samples:
        small_samples[length] = self.samples[length]
      return small_samples

    def show_dropped_samples(self):
      '''
      Print the word lengths that were dropped from the dataset, and the total number of words of each length.
      '''
      dropped_samples = self.dropped_samples()
      print('Dropped Samples \n')
      print('Length    # Samples')
      for key, value in dropped_samples.items():
        print(f'{key:>6} {len(value):>12}')

# Model Definitions



In [6]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')


class CommonModel(nn.Module):
  '''
  This defines the fit, evaluate, and predict functions that are shared between all models.
  It is not instantiated directly but inherited by all other model classes.

  Methods:
    fit: Train model on train dataloader and evaluate on validation dataloader.
         Prints training losses and validation losses. No return.

    evaluate: Calculates losses on evaluation dataloader, prints and returns average loss across whole dataset.

    predict: Returns predictions and true labels from test dataloader.
             Predictions are list of word length with probabilities of each position being syllable break.
             True labels are binary list of word length, with 1 for syllable break and 0 otherwise.
  '''
  def __init__(self):
    super().__init__()

  def fit(self, train_dl, val_dl, epochs, loss_fn, lstm=False):
    if loss_fn == 'bce':
      self.loss_fn = nn.BCEWithLogitsLoss()
    elif loss_fn == 'focal':
      self.loss_fn = sigmoid_focal_loss
    else:
      raise ValueError("loss_fn must either be 'bce' or 'focal'.")
    optimizer = torch.optim.AdamW(self.parameters())
    for epoch in range(epochs):
      running_loss = 0.0
      syllables = 0
      for i, data in enumerate(train_dl):
        optimizer.zero_grad()
        surprisal, syll, lang, word = data
        if lstm:
          surprisal = surprisal.unsqueeze(-1).to(torch.float32).to(device)
          syll = syll.unsqueeze(-1).to(torch.float32).to(device)
        else:
          surprisal = surprisal.unsqueeze(1).to(torch.float32).to(device)
          syll = syll.unsqueeze(1).to(torch.float32).to(device)
        prediction = self.forward(surprisal)
        loss = self.loss_fn(prediction, syll)
        loss.backward()
        optimizer.step()
        running_loss += loss.item()
        if i % 100 == 0 and i != 0:
          print(f'{loss}, [{epoch + 1}, {i + 1:5d}] loss: {running_loss/(i+1)}')
      print()

      val_loss = self.evaluate(val_dl, lstm=lstm)
      print('Validation Loss')
      print(val_loss)
      print()

    return running_loss / (i+1)

  def evaluate(self, val_dl, lstm=False):
    losses = []
    syllables = 0
    with torch.no_grad():
      for data in val_dl:
        surprisal, syll, lang, word = data
        if lstm:
          surprisal = surprisal.unsqueeze(-1).to(torch.float32).to(device)
          syll = syll.unsqueeze(-1).to(torch.float32).to(device)
        else:
          surprisal = surprisal.unsqueeze(1).to(torch.float32).to(device)
          syll = syll.unsqueeze(1).to(torch.float32).to(device)
        prediction = self.forward(surprisal)
        loss = self.loss_fn(prediction, syll)
        losses.append(loss)

    return torch.Tensor(losses).mean()

  def predict(self, test_dl, separate_words=False, lstm=False):
    with torch.no_grad():
      self.eval()
      predictions = []
      syllables = []
      activation = nn.Sigmoid()

      for data in test_dl:
        surprisal, syll, lang, word = data
        if lstm:
          surprisal = surprisal.unsqueeze(-1).to(torch.float32).to(device)
          syll = syll.unsqueeze(-1).to(torch.float32).to(device)
        else:
          surprisal = surprisal.unsqueeze(1).to(torch.float32).to(device)
          syll = syll.unsqueeze(1).to(torch.float32).to(device)
        pred = activation(self.forward(surprisal)).detach().cpu()

        if separate_words:
          if lstm:
            for i in range(syll.shape[0]):
              syllables.append(syll[i,:,0])
              predictions.append(pred[i,:,0])
          else:
            for i in range(syll.shape[0]):
              syllables.append(syll[i,0])
              predictions.append(pred[i,0])
        else:
          syll = syll.cpu().flatten().tolist()
          pred = activation(self.forward(surprisal)).flatten().tolist()
          syllables += syll
          predictions += pred

    return predictions, syllables

  def fit_wandb(self, train_dl, val_dl, epochs, loss_fn, run_name=None, project_name='Decipherment Project', lstm=False):
    if loss_fn == 'bce':
      self.loss_fn = nn.BCEWithLogitsLoss()
    elif loss_fn == 'focal':
      self.loss_fn = sigmoid_focal_loss
    else:
      raise ValueError("loss_fn must either be 'bce' or 'focal'.")

    if run_name:
      name = run_name
    elif lstm is False:
      name = f'{self.architecture}_{self.n_gram}gram_{self.d_hidden}hidden_{self.n_layers}layers_{loss_fn}_loss'
    elif self.bidirectional is True:
      name = f'{self.architecture}_{self.d_hidden}hidden_{self.n_layers}layers_bidirectional_{loss_fn}_loss'
    else:
      name = f'{self.architecture}_{self.d_hidden}hidden_{self.n_layers}layers_unidirectional_{loss_fn}_loss'

    if lstm is False:
      config = {'architecture' : self.architecture,
                'n_gram' : self.n_gram,
                'd_hidden' : self.d_hidden,
                'n_layers' : self.n_layers,
                'loss_fn' : loss_fn,
                'size' : self.size}
    else:
      config = {'architecture' : self.architecture,
                'd_hidden' : self.d_hidden,
                'n_layers' : self.n_layers,
                'loss_fn' : loss_fn,
                'size' : self.size,
                'bidirectional' : self.bidirectional}

    wandb.init(project=project_name,
               name=name,
               config=config)

    for epoch in range(epochs):
      train_loss = self.fit(train_dl, val_dl, epochs=1, loss_fn=loss_fn, lstm=lstm)
      val_loss = self.evaluate(val_dl, lstm=lstm)
      wandb.log({'train_loss': train_loss, 'val_loss': val_loss})



class NgramFNN(CommonModel):
  '''
  Feedforward Neural Network (FNN) that takes an ngram of size n_gram and feeds the surprisals through
  n hidden layers (n_layers) each of dimension d (d_hidden).

  *NOTE* This is implemented using Conv1d layers, however because we lock the kernel_size of all hidden
  layers and the output layer to 1, this is equivalent to a Feedforward Network operating over ngrams.

  Params:
    n_gram:   Size of ngram window to look over
    d_hidden: Dimensionality of hidden layers (equivalent to n_filters in NgramCNN)
    n_layers: Number of hidden layers (not including input and output layers)

  Returns:
    x: List of length of original word showing log-odds for each position to be a syllable break.
       This is converted to probabilities using sigmoid activation in "predict" method.

  Methods:
    See parent class "CommonModel"
  '''
  def __init__(self, n_gram, d_hidden, n_layers):
    super().__init__()

    self.n_gram = n_gram
    self.d_hidden = d_hidden
    self.n_layers = n_layers
    self.architecture = 'fnn'

    self.input_ = nn.Conv1d(in_channels=1, out_channels=d_hidden, kernel_size=n_gram, padding='same')
    self.output = nn.Conv1d(in_channels=d_hidden, out_channels=1, kernel_size=1)
    self.hidden = nn.ModuleList()
    for n in range(n_layers):
      self.hidden.append(nn.Conv1d(in_channels=d_hidden, out_channels=d_hidden, kernel_size=1))
      self.hidden.append(nn.GELU())
    self.activation = nn.GELU()

    self.size = sum(p.numel() for p in self.parameters())

  def forward(self, x):
    x = self.input_(x)
    x = self.activation(x)
    for hidden in self.hidden:
      x = hidden(x)
    x = self.output(x)

    return x



class NgramCNN(CommonModel):
  '''
  Identical to the NgramFNN, except that it applies the same window size (n_gram) to the hidden layers
  as it does to the input layer, resulting in a kind of "recursive" ngram structure that incorporates
  information from more and more neighboring ngrams the deeper the model goes. This is the same as our
  original CNN model.

  Params:
    n_gram:    Size of ngram window to look over
    n_filters: Number of filters to pass over each layer
    n_layers:  Number of hidden layers (not including input and output layers)

  Returns:
    x: List of length of original word showing log-odds for each position to be a syllable break.
       This is converted to probabilities using sigmoid activation in "predict" method.

  Methods:
    See parent class "CommonModel"
  '''
  def __init__(self, n_gram, n_filters, n_layers):
    super().__init__()

    self.n_gram = n_gram
    self.d_hidden = n_filters
    self.n_layers = n_layers
    self.architecture = 'cnn'

    self.input_ = nn.Conv1d(in_channels=1, out_channels=n_filters, kernel_size=n_gram, padding='same')
    self.output = nn.Conv1d(in_channels=n_filters, out_channels=1, kernel_size=1)
    self.hidden = nn.ModuleList()
    for n in range(n_layers):
      self.hidden.append(nn.Conv1d(in_channels=n_filters, out_channels=n_filters, kernel_size=n_gram, padding='same'))
      self.hidden.append(nn.GELU())
    self.activation = nn.GELU()

    self.size = sum(p.numel() for p in self.parameters())

  def forward(self, x):
    x = self.input_(x)
    x = self.activation(x)
    for hidden in self.hidden:
      x = hidden(x)
    x = self.output(x)

    return x


class NgramLSTM(CommonModel):
  def __init__(self,
               hidden_size=5,
               n_layers=1,
               bidirectional=True):
    super().__init__()
    self.lstm = nn.LSTM(input_size=1,
                        hidden_size=hidden_size,
                        num_layers=n_layers,
                        bias=True,
                        batch_first=True,
                        dropout=0.0,
                        bidirectional=bidirectional,
                        proj_size=0,
                        device=None,
                        dtype=None)

    self.d_hidden = hidden_size
    self.n_layers = n_layers
    self.architecture = 'lstm'
    self.bidirectional=bidirectional

    if bidirectional:
      self.linear = nn.Linear(in_features= 2 * hidden_size, out_features=1)
    else:
      self.linear = nn.Linear(in_features=hidden_size, out_features=1)

    self.size = sum(p.numel() for p in self.parameters())

  def forward(self, x):
    x, hidden_out = self.lstm(x)
    x = self.linear(x)

    return x

# Train Models on Original Size Datasets

## All Languages

In [7]:
# Train and Val Datasets for All Languages
with open(os.path.join(data_folder, 'Original', 'All_Langs_Train_Original.pickle'), 'rb') as f:
  train_ds = pickle.load(f)
with open(os.path.join(data_folder, 'Original', 'All_Langs_Val_Original.pickle'), 'rb') as f:
  val_ds = pickle.load(f)
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Original', 'All_Langs_Test_Original.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

### FNN

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

# Train model and log on wandb
fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

# Save model to Drive
torch.save(fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.6261645555496216, [1,   101] loss: 0.6801442374097239
0.49969950318336487, [1,   201] loss: 0.6095519627801221
0.5129373669624329, [1,   301] loss: 0.5652336953486319
0.48109668493270874, [1,   401] loss: 0.5445327947561878
0.4992735683917999, [1,   501] loss: 0.5305178189824917
0.4035862982273102, [1,   601] loss: 0.5195504349103188
0.4791398048400879, [1,   701] loss: 0.5127842255393721
0.500110387802124, [1,   801] loss: 0.5077601276831085
0.3988494873046875, [1,   901] loss: 0.5042221578588496
0.49221786856651306, [1,  1001] loss: 0.4993463391131097
0.4937630891799927, [1,  1101] loss: 0.4960972963274879
0.5032767653465271, [1,  1201] loss: 0.49452423986100236
0.5075018405914307, [1,  1301] loss: 0.4914110073394541
0.47094738483428955, [1,  1401] loss: 0.4894699697235837
0.3467044234275818, [1,  1501] loss: 0.48785841333953484
0.5180473923683167, [1,  1601] loss: 0.48659380462525564
0.4425135552883148, [1,  1701] loss: 0.4852337217782961
0.5222145318984985, [1,  1801] loss: 0.484

In [8]:
#@title Load FNN
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)
fnn_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

<All keys matched successfully>

In [9]:
#@title Validate FNN

# Run predictions on Val Dataloader
val_dl = DataLoader(val_ds, batch_size=1, shuffle=False)
preds, sylls = fnn_model.predict(val_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in val_ds for entry in row[1]]
new_langs = [entry[2] for entry in val_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(val_ds)) for j in range(len(val_ds[id][1]))]
new_positions = [i for entry in val_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in val_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'VAL_All_Langs_FNN_7gram_15hidden_5layers_10epochs_Original'
fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
fnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999996              1        sv             0          0        h
1     0.006008              0        sv             0          1        E
2     0.257698              0        sv             0          2        m
3     0.693426              0        sv             0          3        t
4     0.225256              1        sv             0          4        n
5     0.277617              0        sv             0          5        I
6     0.225761              0        sv             0          6        N
7     0.999956              1        en             1          0        r
8     0.074810              0        en             1          1        1
9     0.554621              1        en             1          2        d

In [ ]:
#@title Evaluate FNN

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = fnn_model.predict(test_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Original'
fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
fnn_output[:10]

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Original'
fnn_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
fnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999986              1        de             0          0        r
1     0.086976              0        de             0          1        o
2     0.629918              1        de             0          2        z
3     0.201749              0        de             0          3        @
4     0.186117              0        de             0          4        n
5     0.766119              1        de             0          5        S
6     0.133671              0        de             0          6        B
7     0.999978              1        tr             1          0        m
8     0.056615              0        tr             1          1        u
9     0.475875              1        tr             1          2        r

### CNN

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

# Train model and log on wandb
cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

# Save model to Drive
torch.save(cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.5483860969543457, [1,   101] loss: 0.6498430141127935
0.5141754746437073, [1,   201] loss: 0.5677863556650741
0.4966910481452942, [1,   301] loss: 0.5294757139346132
0.4651417136192322, [1,   401] loss: 0.5126959931597745
0.4723781943321228, [1,   501] loss: 0.5021981615089847
0.3150939643383026, [1,   601] loss: 0.49220781553902365
0.4696325659751892, [1,   701] loss: 0.486186839565741
0.5153297185897827, [1,   801] loss: 0.48174557199564466
0.26712071895599365, [1,   901] loss: 0.47914973976344827
0.48371368646621704, [1,  1001] loss: 0.4733943291953751
0.4603268504142761, [1,  1101] loss: 0.46913700880352527
0.46662625670433044, [1,  1201] loss: 0.4664834924755644
0.48244723677635193, [1,  1301] loss: 0.4617565020197268
0.4234452247619629, [1,  1401] loss: 0.4584751081075267
0.17784878611564636, [1,  1501] loss: 0.4554842339504726
0.47729235887527466, [1,  1601] loss: 0.4530466649399781
0.3801571726799011, [1,  1701] loss: 0.45058066128528096
0.4875464141368866, [1,  1801] loss: 0

In [10]:
#@title Load CNN
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)
cnn_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

<All keys matched successfully>

In [11]:
#@title Validate CNN

# Run predictions on Val Dataloader
val_dl = DataLoader(val_ds, batch_size=1, shuffle=False)
preds, sylls = cnn_model.predict(val_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in val_ds for entry in row[1]]
new_langs = [entry[2] for entry in val_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(val_ds)) for j in range(len(val_ds[id][1]))]
new_positions = [i for entry in val_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in val_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'VAL_All_Langs_CNN_7gram_15hidden_10layers_10epochs_Original'
cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
cnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     1.000000              1        sv             0          0        h
1     0.000166              0        sv             0          1        E
2     0.235007              0        sv             0          2        m
3     0.621507              0        sv             0          3        t
4     0.309866              1        sv             0          4        n
5     0.208528              0        sv             0          5        I
6     0.005309              0        sv             0          6        N
7     0.999994              1        en             1          0        r
8     0.110165              0        en             1          1        1
9     0.616721              1        en             1          2        d

In [ ]:
#@title Evaluate CNN

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = cnn_model.predict(test_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Original'
cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
cnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     1.000000              1        de             0          0        r
1     0.027287              0        de             0          1        o
2     0.820508              1        de             0          2        z
3     0.138348              0        de             0          3        @
4     0.465263              0        de             0          4        n
5     0.457991              1        de             0          5        S
6     0.013605              0        de             0          6        B
7     0.999994              1        tr             1          0        m
8     0.019614              0        tr             1          1        u
9     0.696653              1        tr             1          2        r

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Original'
cnn_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
cnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999941              1        tr             0          0        h
1     0.133496              0        tr             0          1        a
2     0.517738              1        tr             0          2        s
3     0.499876              0        tr             0          3        u
4     0.024131              0        tr             0          4        t
5     0.999976              1        no             1          0        m
6     0.052353              0        no             1          1        Y
7     0.625859              1        no             1          2        s
8     0.266597              0        no             1          3        t
9     0.454203              0        no             1          4        I

### LSTM

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

# Train model and log on wandb
lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

# Save model to Drive
torch.save(lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.5951150059700012, [1,   101] loss: 0.6429732973032659
0.5398638248443604, [1,   201] loss: 0.5925090046071294
0.5072588920593262, [1,   301] loss: 0.5516283206666427
0.4696715474128723, [1,   401] loss: 0.5308546370030044
0.47912275791168213, [1,   501] loss: 0.5176910047759553
0.31808796525001526, [1,   601] loss: 0.5055451055433905
0.4693785607814789, [1,   701] loss: 0.498191208944001
0.5186825394630432, [1,   801] loss: 0.4925838399320357
0.27042505145072937, [1,   901] loss: 0.489455517799026
0.508285403251648, [1,  1001] loss: 0.48342245619196994
0.4656975269317627, [1,  1101] loss: 0.4797126092727243
0.4925461709499359, [1,  1201] loss: 0.4787786105255302
0.508342444896698, [1,  1301] loss: 0.47536288389075637
0.4796450436115265, [1,  1401] loss: 0.4734789919770249
0.16350606083869934, [1,  1501] loss: 0.4715351075539583
0.5126874446868896, [1,  1601] loss: 0.4704772966037237
0.4108915627002716, [1,  1701] loss: 0.4692794978049207
0.5215423107147217, [1,  1801] loss: 0.4687900

In [12]:
#@title Load LSTM
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Original'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original'

lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)
lstm_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

<All keys matched successfully>

In [13]:
#@title Validate LSTM

# Run predictions on Val Dataloader
val_dl = DataLoader(val_ds, batch_size=1, shuffle=False)
preds, sylls = lstm_model.predict(val_dl, separate_words=True, lstm=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in val_ds for entry in row[1]]
new_langs = [entry[2] for entry in val_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(val_ds)) for j in range(len(val_ds[id][1]))]
new_positions = [i for entry in val_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in val_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'VAL_All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Original'
lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
lstm_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999730              1        sv             0          0        h
1     0.000449              0        sv             0          1        E
2     0.313673              0        sv             0          2        m
3     0.508743              0        sv             0          3        t
4     0.367589              1        sv             0          4        n
5     0.329363              0        sv             0          5        I
6     0.008282              0        sv             0          6        N
7     0.999874              1        en             1          0        r
8     0.062394              0        en             1          1        1
9     0.575013              1        en             1          2        d

In [ ]:
#@title Evaluate LSTM

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = lstm_model.predict(test_dl, separate_words=True, lstm=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Original'
lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
lstm_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999787              1        de             0          0        r
1     0.002648              0        de             0          1        o
2     0.814588              1        de             0          2        z
3     0.123189              0        de             0          3        @
4     0.351021              0        de             0          4        n
5     0.571853              1        de             0          5        S
6     0.004870              0        de             0          6        B
7     0.999733              1        tr             1          0        m
8     0.010456              0        tr             1          1        u
9     0.726056              1        tr             1          2        r

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Original'
lstm_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
lstm_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999938              1        tr             0          0        h
1     0.027116              0        tr             0          1        a
2     0.340925              1        tr             0          2        s
3     0.642206              0        tr             0          3        u
4     0.010387              0        tr             0          4        t
5     0.999780              1        no             1          0        m
6     0.000917              0        no             1          1        Y
7     0.879884              1        no             1          2        s
8     0.097371              0        no             1          3        t
9     0.631646              0        no             1          4        I

## Leave One Out (LOO)

We resample the Train and Val datasets to create a new Train set of all-but-one languages and a Val set of the left-out language. The Test dataset remains the same (i.e. it is a separate subsample of all languages), but for evaluation purposes are only interested in how the model performs on those examples in the Test set that are from the left-out language. So we make predictions on the entire dataset, but will only count the predictions on the left-out language when calculating MCC and other metrics.

By combining the original Train and Val set together, we are able to create a new LOO Train set for each language that is the same size as the All Language Train set (502,994 words). The two exceptions to this are the LOO datasets for Dutch (460,355 words) and Swedish (478,275 words); because these languages comprise such a large percentage of the All Language Train set, removing them results in a smaller Train dataset even when adding in samples of other languages from the Val set.

**Note:** Though we are using a separate Val dataset to track model performance on the left-out language, in practice with an *unknown language* this would not be possible, since presumably there would be no labeled data for the unknown language. And while we set our model parameters based on the All Language Val dataset (where we take for granted that we know all languages involved), training for only 10 epochs is informed by the fact that we can see the models overfitting on the LOO Val datasets, which again would not be information we would have in practice. (Also, we actually originally saw this on a previous LOO Test dataset, which was a case of unintentional data peeking, and is part of the reason we're setting up new Train / Val / Test datasets for all models and training regimens).

In [ ]:
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Original', 'All_Langs_Test_Original.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Train_Original.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Val_Original.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_FNN_Original'
  loo_fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

  # Train model and log on wandb
  loo_fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

  # Save model to Drive
  torch.save(loo_fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_fnn_model.predict(test_dl, separate_words=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.6292620897293091, [1,   101] loss: 0.6788551122835367
0.46498778462409973, [1,   201] loss: 0.6082698007424673
0.4297949969768524, [1,   301] loss: 0.5647339874327777
0.4945123493671417, [1,   401] loss: 0.5434600926396853
0.48330259323120117, [1,   501] loss: 0.5292536161259976
0.5151883959770203, [1,   601] loss: 0.5197832365202626
0.4671945571899414, [1,   701] loss: 0.513266214035377
0.5439704656600952, [1,   801] loss: 0.5074371287736404
0.38650286197662354, [1,   901] loss: 0.5022721250234513
0.5168015956878662, [1,  1001] loss: 0.49885544678071636
0.4951421022415161, [1,  1101] loss: 0.4954669552023686
0.3442859649658203, [1,  1201] loss: 0.4927312939316903
0.41210314631462097, [1,  1301] loss: 0.49113899266646516
0.4754648804664612, [1,  1401] loss: 0.48868831059364315
0.4555422067642212, [1,  1501] loss: 0.4872645099090783
0.39308831095695496, [1,  1601] loss: 0.4859019302990495
0.4554738402366638, [1,  1701] loss: 0.484878943754532
0.4432939887046814, [1,  1801] loss: 0.484

0.6350753903388977, [1,   101] loss: 0.6798326986851079
0.5368916988372803, [1,   201] loss: 0.6071828461405057
0.49920278787612915, [1,   301] loss: 0.5681323722945495
0.5015686750411987, [1,   401] loss: 0.5450513828127759
0.4381260573863983, [1,   501] loss: 0.5312887988761513
0.5330191254615784, [1,   601] loss: 0.5219181456204857
0.44943326711654663, [1,   701] loss: 0.5141557592170555
0.4674466848373413, [1,   801] loss: 0.5092450627189749
0.5483876466751099, [1,   901] loss: 0.5057843367379989
0.5065996646881104, [1,  1001] loss: 0.5027255937680378
0.4563693702220917, [1,  1101] loss: 0.4992405291744842
0.4198393225669861, [1,  1201] loss: 0.49663708886933466
0.45098409056663513, [1,  1301] loss: 0.49519931053675476
0.5058483481407166, [1,  1401] loss: 0.4939917723763253
0.43940430879592896, [1,  1501] loss: 0.49238767600472494
0.50347900390625, [1,  1601] loss: 0.49091376534556685
0.5155567526817322, [1,  1701] loss: 0.48988916881290484
0.369745671749115, [1,  1801] loss: 0.488

0.6310180425643921, [1,   101] loss: 0.6784610400105467
0.4589887261390686, [1,   201] loss: 0.6064909113876855
0.39967429637908936, [1,   301] loss: 0.565198210980805
0.5258196592330933, [1,   401] loss: 0.5445286089791324
0.4495878517627716, [1,   501] loss: 0.5317666916671151
0.4418697953224182, [1,   601] loss: 0.5229417659875358
0.41277074813842773, [1,   701] loss: 0.515223286248818
0.42293640971183777, [1,   801] loss: 0.5095093335477303
0.470523476600647, [1,   901] loss: 0.5047598207301226
0.4652802050113678, [1,  1001] loss: 0.5012904399043911
0.4397874176502228, [1,  1101] loss: 0.49810777053737726
0.4351653456687927, [1,  1201] loss: 0.49538871524335937
0.43903693556785583, [1,  1301] loss: 0.492998823626604
0.39674076437950134, [1,  1401] loss: 0.4915304951885613
0.46121007204055786, [1,  1501] loss: 0.48977827851094063
0.527091920375824, [1,  1601] loss: 0.488167927106569
0.43980228900909424, [1,  1701] loss: 0.48695296331197635
0.5210840106010437, [1,  1801] loss: 0.4859

0.6397640109062195, [1,   101] loss: 0.6793899919727061
0.54231196641922, [1,   201] loss: 0.6068213037887022
0.5542437434196472, [1,   301] loss: 0.5619483584185375
0.49029722809791565, [1,   401] loss: 0.5388805605378234
0.48602136969566345, [1,   501] loss: 0.5255588304972696
0.5791606903076172, [1,   601] loss: 0.5149257128032393
0.48088449239730835, [1,   701] loss: 0.5081845178413663
0.35253167152404785, [1,   801] loss: 0.5035495650902223
0.4964367151260376, [1,   901] loss: 0.4996347166721882
0.47607797384262085, [1,  1001] loss: 0.49653789353418304
0.4616798758506775, [1,  1101] loss: 0.49354878663475354
0.5303457379341125, [1,  1201] loss: 0.49085881288700756
0.4322042763233185, [1,  1301] loss: 0.4889779214580457
0.4797934293746948, [1,  1401] loss: 0.487388289863939
0.3248196244239807, [1,  1501] loss: 0.48590050071855134
0.39060306549072266, [1,  1601] loss: 0.48435108155142437
0.5535963177680969, [1,  1701] loss: 0.48287508306014126
0.458917498588562, [1,  1801] loss: 0.4

0.642478346824646, [1,   101] loss: 0.6787005320633992
0.5429019927978516, [1,   201] loss: 0.6077711318262774
0.4824507534503937, [1,   301] loss: 0.5661377120651676
0.48883527517318726, [1,   401] loss: 0.5441413037200223
0.4958718419075012, [1,   501] loss: 0.5309909385240482
0.4991209805011749, [1,   601] loss: 0.5231595882857699
0.466734379529953, [1,   701] loss: 0.5150415150398194
0.43506568670272827, [1,   801] loss: 0.5102251400513
0.4978962540626526, [1,   901] loss: 0.5061391361479489
0.46140432357788086, [1,  1001] loss: 0.502340415706644
0.36194199323654175, [1,  1101] loss: 0.49951078285963074
0.5317575931549072, [1,  1201] loss: 0.49649578447048115
0.48468536138534546, [1,  1301] loss: 0.49426711107289945
0.5459713935852051, [1,  1401] loss: 0.4929194046207022
0.3639954924583435, [1,  1501] loss: 0.49056636111725177
0.47249430418014526, [1,  1601] loss: 0.48906223687211253
0.4833688735961914, [1,  1701] loss: 0.48742425546864776
0.4572353661060333, [1,  1801] loss: 0.486

...

0.6456217765808105, [1,   101] loss: 0.6777881307177024
0.4697284698486328, [1,   201] loss: 0.605073123428952
0.5269769430160522, [1,   301] loss: 0.5626233150792677
0.4713743329048157, [1,   401] loss: 0.5413674626713084
0.5170539617538452, [1,   501] loss: 0.530067269019262
0.48530927300453186, [1,   601] loss: 0.5206655352663081
0.5084014534950256, [1,   701] loss: 0.5145286378608791
0.35848885774612427, [1,   801] loss: 0.5092806938510114
0.4925459325313568, [1,   901] loss: 0.504283984083182
0.5183082818984985, [1,  1001] loss: 0.5009404943956361
0.45487964153289795, [1,  1101] loss: 0.49823697770757097
0.39998599886894226, [1,  1201] loss: 0.4953844515757199
0.42564210295677185, [1,  1301] loss: 0.49285235846390824
0.4582298696041107, [1,  1401] loss: 0.4913847486114264
0.4615366756916046, [1,  1501] loss: 0.4898991003721893
0.5327421426773071, [1,  1601] loss: 0.48832451758311735
0.36505308747291565, [1,  1701] loss: 0.48633810610612793
0.48299679160118103, [1,  1801] loss: 0.4

0.6523877382278442, [1,   101] loss: 0.6822659898512434
0.4578290581703186, [1,   201] loss: 0.6231498211177428
0.5563728213310242, [1,   301] loss: 0.5756307943318769
0.48479968309402466, [1,   401] loss: 0.5500117376112283
0.4561406672000885, [1,   501] loss: 0.5361014263715572
0.5442569851875305, [1,   601] loss: 0.5263736421078097
0.3572677671909332, [1,   701] loss: 0.5171571246184908
0.5172238349914551, [1,   801] loss: 0.5123360170965338
0.4829685389995575, [1,   901] loss: 0.5072659628008896
0.36642739176750183, [1,  1001] loss: 0.5024082670053402
0.4589686989784241, [1,  1101] loss: 0.4984170122648996
0.49862930178642273, [1,  1201] loss: 0.4960539516163905
0.41896852850914, [1,  1301] loss: 0.49310610088864076
0.5658280849456787, [1,  1401] loss: 0.4917540657762797
0.4927462935447693, [1,  1501] loss: 0.4902409818135127
0.47706058621406555, [1,  1601] loss: 0.4890914174130676
0.5055811405181885, [1,  1701] loss: 0.48758493453211676
0.4229855537414551, [1,  1801] loss: 0.48683

0.6293083429336548, [1,   101] loss: 0.6786651068394727
0.4988304376602173, [1,   201] loss: 0.6054425607273235
0.42686977982521057, [1,   301] loss: 0.564007928601135
0.5082870721817017, [1,   401] loss: 0.5412363089676807
0.47313305735588074, [1,   501] loss: 0.5269314768963945
0.49564361572265625, [1,   601] loss: 0.5187863307120201
0.4585123360157013, [1,   701] loss: 0.5112756375281855
0.5025796294212341, [1,   801] loss: 0.5061370749189315
0.541214108467102, [1,   901] loss: 0.5017921262886892
0.36448782682418823, [1,  1001] loss: 0.49784782566092944
0.45080098509788513, [1,  1101] loss: 0.495600189908757
0.4089488685131073, [1,  1201] loss: 0.4933158887191974
0.414178729057312, [1,  1301] loss: 0.4908552678684195
0.4188200831413269, [1,  1401] loss: 0.4891111619403582
0.37960878014564514, [1,  1501] loss: 0.48772162948545816
0.5168173313140869, [1,  1601] loss: 0.4866386030164828
0.4442227780818939, [1,  1701] loss: 0.4853092153534197
0.4580829441547394, [1,  1801] loss: 0.48395

0.5905788540840149, [1,   101] loss: 0.6776969066940912
0.43437063694000244, [1,   201] loss: 0.6064599340234823
0.5369588136672974, [1,   301] loss: 0.5658797170236657
0.45307210087776184, [1,   401] loss: 0.5419920896205521
0.4870559871196747, [1,   501] loss: 0.5295945868163765
0.38161125779151917, [1,   601] loss: 0.5199881652726508
0.5688338279724121, [1,   701] loss: 0.5137794780493122
0.5510439872741699, [1,   801] loss: 0.5086142013358713
0.4978102147579193, [1,   901] loss: 0.5043828030272938
0.4214550852775574, [1,  1001] loss: 0.501382286493833
0.5194747447967529, [1,  1101] loss: 0.49923438564633155
0.4782593846321106, [1,  1201] loss: 0.4970206237156921
0.46579301357269287, [1,  1301] loss: 0.49469158225202453
0.34762275218963623, [1,  1401] loss: 0.4930207592984934
0.42673230171203613, [1,  1501] loss: 0.49169154914913776
0.5051956176757812, [1,  1601] loss: 0.49004920689781184
0.5016140341758728, [1,  1701] loss: 0.48927095942396337
0.4657094478607178, [1,  1801] loss: 0

0.6141902208328247, [1,   101] loss: 0.6791629384059718
0.5068270564079285, [1,   201] loss: 0.5970278838973734
0.43027162551879883, [1,   301] loss: 0.5549156721248183
0.5276647210121155, [1,   401] loss: 0.5360082943094638
0.5413209199905396, [1,   501] loss: 0.5257778836343578
0.5036776661872864, [1,   601] loss: 0.5176939681147577
0.46239495277404785, [1,   701] loss: 0.5104559190603194
0.46719759702682495, [1,   801] loss: 0.5050091051058228
0.4804617166519165, [1,   901] loss: 0.5003899963992285
0.4907797873020172, [1,  1001] loss: 0.4968342831680229
0.45298510789871216, [1,  1101] loss: 0.49488593441697276
0.4679202735424042, [1,  1201] loss: 0.49189568407132567
0.5423324108123779, [1,  1301] loss: 0.4903738676218873
0.5268415212631226, [1,  1401] loss: 0.48821384042267457
0.4465389847755432, [1,  1501] loss: 0.4858615354130381
0.46435680985450745, [1,  1601] loss: 0.48455482751112444
0.49932846426963806, [1,  1701] loss: 0.48269501370517454
0.537722110748291, [1,  1801] loss: 0

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Train_Original.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Val_Original.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_CNN_Original'
  loo_cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

  # Train model and log on wandb
  loo_cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

  # Save model to Drive
  torch.save(loo_cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_cnn_model.predict(test_dl, separate_words=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.6126949787139893, [1,   101] loss: 0.6601290100871926
0.45984819531440735, [1,   201] loss: 0.5807788793127335
0.3800783157348633, [1,   301] loss: 0.5402067541284022
0.49254629015922546, [1,   401] loss: 0.5212366920605562
0.46522995829582214, [1,   501] loss: 0.5077478177176264
0.5368314981460571, [1,   601] loss: 0.4995178890456376
0.46342262625694275, [1,   701] loss: 0.49361827952545484
0.5447779893875122, [1,   801] loss: 0.4879569411091739
0.29965537786483765, [1,   901] loss: 0.48311334064480466
0.5316559076309204, [1,  1001] loss: 0.47982888365839865
0.47494202852249146, [1,  1101] loss: 0.47551772865948083
0.2734934687614441, [1,  1201] loss: 0.47119517889894313
0.35741180181503296, [1,  1301] loss: 0.46791366376068666
0.4419126510620117, [1,  1401] loss: 0.46391214062323494
0.4154282212257385, [1,  1501] loss: 0.46104303870020036
0.32094094157218933, [1,  1601] loss: 0.45840391352875093
0.4215840697288513, [1,  1701] loss: 0.4561455473172391
0.39787644147872925, [1,  1801]

0.5743474960327148, [1,   101] loss: 0.6505229892116962
0.5460945963859558, [1,   201] loss: 0.5690203399504002
0.4971604347229004, [1,   301] loss: 0.5357790552698497
0.4935898780822754, [1,   401] loss: 0.5141732552996895
0.41364043951034546, [1,   501] loss: 0.5031530082582714
0.5067748427391052, [1,   601] loss: 0.4944133523994198
0.40475377440452576, [1,   701] loss: 0.4864196238266078
0.4313415288925171, [1,   801] loss: 0.48138098117340816
0.5497661232948303, [1,   901] loss: 0.47722501101821957
0.49151039123535156, [1,  1001] loss: 0.4735366932370446
0.4151885211467743, [1,  1101] loss: 0.46905061973429724
0.35296544432640076, [1,  1201] loss: 0.4652278865257171
0.4123557507991791, [1,  1301] loss: 0.46282741333501876
0.47433724999427795, [1,  1401] loss: 0.4607561077287076
0.39644840359687805, [1,  1501] loss: 0.45795566891925005
0.46170902252197266, [1,  1601] loss: 0.45547251853810333
0.46888676285743713, [1,  1701] loss: 0.45365041567079467
0.3020603656768799, [1,  1801] lo

0.5799727439880371, [1,   101] loss: 0.6500392662416591
0.4729434549808502, [1,   201] loss: 0.5710080682638272
0.27256178855895996, [1,   301] loss: 0.5372687551468314
0.5097927451133728, [1,   401] loss: 0.5215118378772403
0.45274749398231506, [1,   501] loss: 0.5105931495359082
0.37221014499664307, [1,   601] loss: 0.5017773342410261
0.3351762890815735, [1,   701] loss: 0.49386568144282667
0.39001163840293884, [1,   801] loss: 0.4881072310398283
0.45688194036483765, [1,   901] loss: 0.48354047225926744
0.44252675771713257, [1,  1001] loss: 0.47996445881439137
0.419825941324234, [1,  1101] loss: 0.4759138260750636
0.3845212161540985, [1,  1201] loss: 0.47143505375947087
0.36523622274398804, [1,  1301] loss: 0.46737506206818125
0.34861433506011963, [1,  1401] loss: 0.4645210504106417
0.4070582091808319, [1,  1501] loss: 0.4612794617547106
0.48120608925819397, [1,  1601] loss: 0.4581934746115153
0.403990238904953, [1,  1701] loss: 0.4558474006966799
0.4548245370388031, [1,  1801] loss:

0.5931305289268494, [1,   101] loss: 0.6520158630786556
0.5287823677062988, [1,   201] loss: 0.5715063427811238
0.549892246723175, [1,   301] loss: 0.528899903016233
0.46330156922340393, [1,   401] loss: 0.5105425871518484
0.42743825912475586, [1,   501] loss: 0.4992896107856385
0.5403409004211426, [1,   601] loss: 0.4891695936834951
0.45044875144958496, [1,   701] loss: 0.4832617692362395
0.2251947969198227, [1,   801] loss: 0.4794595626818851
0.4686301648616791, [1,   901] loss: 0.47672608817258766
0.44941893219947815, [1,  1001] loss: 0.47338103411438226
0.4371337294578552, [1,  1101] loss: 0.4687955772654778
0.48499536514282227, [1,  1201] loss: 0.46403760139789313
0.37603673338890076, [1,  1301] loss: 0.46042840477139285
0.41145163774490356, [1,  1401] loss: 0.4573199113061137
0.20824477076530457, [1,  1501] loss: 0.4544960507784265
0.3117038905620575, [1,  1601] loss: 0.45171308362022333
0.5048467516899109, [1,  1701] loss: 0.4490574902467767
0.4125540852546692, [1,  1801] loss: 

0.5703277587890625, [1,   101] loss: 0.6551881975466662
0.5577167868614197, [1,   201] loss: 0.5727091590266916
0.49452441930770874, [1,   301] loss: 0.5352584613716087
0.4702039361000061, [1,   401] loss: 0.5150121947625034
0.47289615869522095, [1,   501] loss: 0.5032803815401005
0.4899419844150543, [1,   601] loss: 0.496695248388411
0.47202834486961365, [1,   701] loss: 0.4890185412598745
0.38670778274536133, [1,   801] loss: 0.484798328595215
0.49282991886138916, [1,   901] loss: 0.48054828536960315
0.40906286239624023, [1,  1001] loss: 0.4758898251421087
0.2678954005241394, [1,  1101] loss: 0.4717744821640278
0.4899967610836029, [1,  1201] loss: 0.4669518642108903
0.4338077902793884, [1,  1301] loss: 0.4632647962386016
0.4886574447154999, [1,  1401] loss: 0.46075244025619094
0.2549643814563751, [1,  1501] loss: 0.45686464737368615
0.44874635338783264, [1,  1601] loss: 0.45423206325846116
0.4183429777622223, [1,  1701] loss: 0.45148130791422764
0.4098687171936035, [1,  1801] loss: 0

...

0.633242666721344, [1,   101] loss: 0.6637792174178775
0.4559464454650879, [1,   201] loss: 0.5872430813253222
0.5207045078277588, [1,   301] loss: 0.5446951145745591
0.45560696721076965, [1,   401] loss: 0.5251525088290027
0.4897325932979584, [1,   501] loss: 0.5144611221111701
0.4422590732574463, [1,   601] loss: 0.5034205476426443
0.5171403288841248, [1,   701] loss: 0.49803903061211025
0.2613523602485657, [1,   801] loss: 0.49285894647222034
0.49881288409233093, [1,   901] loss: 0.48742957547158167
0.5234519839286804, [1,  1001] loss: 0.48421419393289816
0.3983396887779236, [1,  1101] loss: 0.48128967191499544
0.3504219949245453, [1,  1201] loss: 0.47639220928793446
0.36992284655570984, [1,  1301] loss: 0.47186022591157933
0.4415131211280823, [1,  1401] loss: 0.46855657083181124
0.4150288701057434, [1,  1501] loss: 0.4652273250069918
0.5091157555580139, [1,  1601] loss: 0.4620795429734831
0.30376917123794556, [1,  1701] loss: 0.4585358949683646
0.43994250893592834, [1,  1801] loss:

0.6280409693717957, [1,   101] loss: 0.65400232182871
0.4298804998397827, [1,   201] loss: 0.5710698146725175
0.566926121711731, [1,   301] loss: 0.532090268657849
0.4700239300727844, [1,   401] loss: 0.5120973089463693
0.4205520749092102, [1,   501] loss: 0.5021743475498553
0.561176598072052, [1,   601] loss: 0.4943430247203681
0.2864267826080322, [1,   701] loss: 0.48680307092238084
0.5451072454452515, [1,   801] loss: 0.4840791957283139
0.477542519569397, [1,   901] loss: 0.4790149605300662
0.3087690770626068, [1,  1001] loss: 0.4730358048305883
0.39942774176597595, [1,  1101] loss: 0.467936505021343
0.44837045669555664, [1,  1201] loss: 0.46426646210420736
0.34359011054039, [1,  1301] loss: 0.4596935647735222
0.5097315311431885, [1,  1401] loss: 0.4570375277602953
0.44918251037597656, [1,  1501] loss: 0.45437434845809377
0.4187018871307373, [1,  1601] loss: 0.45224835450466094
0.4602600634098053, [1,  1701] loss: 0.44977220291954007
0.3590054512023926, [1,  1801] loss: 0.4479731878

0.5573081970214844, [1,   101] loss: 0.6427236022335467
0.482835978269577, [1,   201] loss: 0.5597889580536838
0.3371402323246002, [1,   301] loss: 0.5242486748584482
0.49817100167274475, [1,   401] loss: 0.5055664208464492
0.49996405839920044, [1,   501] loss: 0.4954618226268334
0.4908255934715271, [1,   601] loss: 0.4901117361127438
0.4532860517501831, [1,   701] loss: 0.4845044619049053
0.49775245785713196, [1,   801] loss: 0.4799263599734479
0.542284369468689, [1,   901] loss: 0.4761907800817066
0.26114851236343384, [1,  1001] loss: 0.47340872085892355
0.42821985483169556, [1,  1101] loss: 0.4720571390966412
0.3338088393211365, [1,  1201] loss: 0.4698384386440002
0.3960469663143158, [1,  1301] loss: 0.4673561794106361
0.3783867061138153, [1,  1401] loss: 0.46475268242020507
0.30869558453559875, [1,  1501] loss: 0.4623078498976934
0.5029357075691223, [1,  1601] loss: 0.4601466496574514
0.4085880219936371, [1,  1701] loss: 0.4577290435737193
0.42096152901649475, [1,  1801] loss: 0.45

0.5436702966690063, [1,   101] loss: 0.6574278261401866
0.34137293696403503, [1,   201] loss: 0.5792365043020961
0.5386614203453064, [1,   301] loss: 0.5390815766051759
0.4472625255584717, [1,   401] loss: 0.5148067931061671
0.4912874400615692, [1,   501] loss: 0.5024823969352745
0.311805784702301, [1,   601] loss: 0.49289315775309545
0.5624266862869263, [1,   701] loss: 0.48684616231714267
0.5471673011779785, [1,   801] loss: 0.48165887263086105
0.49816304445266724, [1,   901] loss: 0.4777037330658137
0.3771747052669525, [1,  1001] loss: 0.4752062982046878
0.541703462600708, [1,  1101] loss: 0.4735158107342447
0.44806987047195435, [1,  1201] loss: 0.4712012845287712
0.43581128120422363, [1,  1301] loss: 0.46817433911960554
0.22715212404727936, [1,  1401] loss: 0.46513712918817957
0.366085022687912, [1,  1501] loss: 0.4628401439162908
0.4271722435951233, [1,  1601] loss: 0.4598802602119851
0.4630085527896881, [1,  1701] loss: 0.45803314156563124
0.4177895486354828, [1,  1801] loss: 0.4

0.5919453501701355, [1,   101] loss: 0.6545830321784066
0.4856361448764801, [1,   201] loss: 0.5815241443577097
0.3971668481826782, [1,   301] loss: 0.537236266159932
0.5171771049499512, [1,   401] loss: 0.5185344085431753
0.5639692544937134, [1,   501] loss: 0.5101092220423464
0.48908519744873047, [1,   601] loss: 0.5022652480943429
0.44367390871047974, [1,   701] loss: 0.49429899772971914
0.4438220262527466, [1,   801] loss: 0.48894458771049604
0.4487369656562805, [1,   901] loss: 0.48403275279239333
0.4777335524559021, [1,  1001] loss: 0.47941288048332625
0.4654788672924042, [1,  1101] loss: 0.47798924937126963
0.4620134234428406, [1,  1201] loss: 0.47414596563671946
0.5599232316017151, [1,  1301] loss: 0.4725330582405401
0.4978135824203491, [1,  1401] loss: 0.4696169240210075
0.41757816076278687, [1,  1501] loss: 0.46622833607099123
0.42190396785736084, [1,  1601] loss: 0.4637715948988764
0.42668792605400085, [1,  1701] loss: 0.46051488377412303
0.5110766291618347, [1,  1801] loss:

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Train_Original.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Original', 'LOO', f'LOO_{lang[1]}_Val_Original.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_LSTM_Original'
  loo_lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

  # Train model and log on wandb
  loo_lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

  # Save model to Drive
  torch.save(loo_lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_lstm_model.predict(test_dl, separate_words=True, lstm=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.596551775932312, [1,   101] loss: 0.6390347628310176
0.5031380653381348, [1,   201] loss: 0.5914922147544462
0.38342687487602234, [1,   301] loss: 0.5522712946334154
0.4907103180885315, [1,   401] loss: 0.5312356392567295
0.4650764763355255, [1,   501] loss: 0.5166860981556232
0.5355891585350037, [1,   601] loss: 0.5067238508415302
0.4626496732234955, [1,   701] loss: 0.5000144059367254
0.5459811091423035, [1,   801] loss: 0.49373515938105206
0.3057807981967926, [1,   901] loss: 0.4880905860040614
0.5366420745849609, [1,  1001] loss: 0.4845328595969346
0.48122379183769226, [1,  1101] loss: 0.48101043406126176
0.2654699385166168, [1,  1201] loss: 0.47863850655107076
0.3786765933036804, [1,  1301] loss: 0.47720836988327414
0.48241740465164185, [1,  1401] loss: 0.4747772695633618
0.44250816106796265, [1,  1501] loss: 0.47374306583428366
0.35832229256629944, [1,  1601] loss: 0.47240988006448836
0.4451003670692444, [1,  1701] loss: 0.47159088754709994
0.42496758699417114, [1,  1801] loss:

0.601908266544342, [1,   101] loss: 0.6416295318320246
0.5678693652153015, [1,   201] loss: 0.5908043615853609
0.4994887411594391, [1,   301] loss: 0.5551489580707296
0.49757781624794006, [1,   401] loss: 0.5307678694736928
0.4117705225944519, [1,   501] loss: 0.5164442717612623
0.5133011937141418, [1,   601] loss: 0.5062483625979273
0.4161287248134613, [1,   701] loss: 0.497261856617499
0.4536898136138916, [1,   801] loss: 0.49230234440271925
0.5502121448516846, [1,   901] loss: 0.48845356147111985
0.4978422224521637, [1,  1001] loss: 0.4853513412899547
0.4295806884765625, [1,  1101] loss: 0.481309887776312
0.3807446360588074, [1,  1201] loss: 0.4782580535340865
0.45897892117500305, [1,  1301] loss: 0.47708284676785107
0.4997361898422241, [1,  1401] loss: 0.47627962182816397
0.42893245816230774, [1,  1501] loss: 0.4744353264143354
0.5150549411773682, [1,  1601] loss: 0.4726580565447438
0.5034215450286865, [1,  1701] loss: 0.47190937900511676
0.2765202820301056, [1,  1801] loss: 0.4707

0.5986685156822205, [1,   101] loss: 0.6413171524458593
0.5122742056846619, [1,   201] loss: 0.5916025628201405
0.2813507318496704, [1,   301] loss: 0.5550315888518115
0.5148109793663025, [1,   401] loss: 0.5350651657603626
0.4593040347099304, [1,   501] loss: 0.5225858872611365
0.38474202156066895, [1,   601] loss: 0.512813255302422
0.3369443118572235, [1,   701] loss: 0.5042613067381222
0.40277180075645447, [1,   801] loss: 0.4980686035253731
0.4627307653427124, [1,   901] loss: 0.49300722193208574
0.44123658537864685, [1,  1001] loss: 0.48938894360423923
0.4546811580657959, [1,  1101] loss: 0.4862759135440195
0.43035364151000977, [1,  1201] loss: 0.4830579279947539
0.40018612146377563, [1,  1301] loss: 0.4803700692132745
0.353687047958374, [1,  1401] loss: 0.479080306423255
0.44979891180992126, [1,  1501] loss: 0.477485269253489
0.5018624067306519, [1,  1601] loss: 0.4755007155858525
0.3822194039821625, [1,  1701] loss: 0.4743403975426415
0.5289532542228699, [1,  1801] loss: 0.47349

0.6090311408042908, [1,   101] loss: 0.6419934904811406
0.5496649742126465, [1,   201] loss: 0.5897075476041481
0.5512727499008179, [1,   301] loss: 0.5478263940426994
0.4671171009540558, [1,   401] loss: 0.5255948480896819
0.43072471022605896, [1,   501] loss: 0.5126574334805597
0.5492956042289734, [1,   601] loss: 0.5015567986669636
0.46648934483528137, [1,   701] loss: 0.49484325992142764
0.24127236008644104, [1,   801] loss: 0.49024745250834656
0.47501206398010254, [1,   901] loss: 0.48687630170722646
0.48447343707084656, [1,  1001] loss: 0.48389486355202777
0.48710617423057556, [1,  1101] loss: 0.48102794043537056
0.5284997820854187, [1,  1201] loss: 0.47775853399829404
0.4463880658149719, [1,  1301] loss: 0.47577589835046713
0.4426302909851074, [1,  1401] loss: 0.4741859928911537
0.18937987089157104, [1,  1501] loss: 0.4727923417839902
0.311845988035202, [1,  1601] loss: 0.4712994918599492
0.5564293265342712, [1,  1701] loss: 0.46952551616895627
0.44545778632164, [1,  1801] loss:

0.5950436592102051, [1,   101] loss: 0.642977798929309
0.5765751600265503, [1,   201] loss: 0.5938971720228148
0.5089149475097656, [1,   301] loss: 0.5546735169186544
0.4775743782520294, [1,   401] loss: 0.5317682798886835
0.4787437915802002, [1,   501] loss: 0.5179535338205253
0.49577227234840393, [1,   601] loss: 0.5101624796920132
0.4769397974014282, [1,   701] loss: 0.5011264898212422
0.3913530707359314, [1,   801] loss: 0.49617478621660843
0.5081461071968079, [1,   901] loss: 0.49150805686343124
0.43828022480010986, [1,  1001] loss: 0.4871470610816757
0.2571758031845093, [1,  1101] loss: 0.4839746228247529
0.5221322178840637, [1,  1201] loss: 0.4802892655754566
0.48110267519950867, [1,  1301] loss: 0.4777930176642929
0.5215228796005249, [1,  1401] loss: 0.4763322298991348
0.2570090889930725, [1,  1501] loss: 0.47289196102024317
0.44195157289505005, [1,  1601] loss: 0.46994116422554466
0.43274986743927, [1,  1701] loss: 0.4665060200274586
0.41135841608047485, [1,  1801] loss: 0.464

...

0.61793053150177, [1,   101] loss: 0.6351090861429082
0.49497735500335693, [1,   201] loss: 0.5864736163497564
0.5199530720710754, [1,   301] loss: 0.5470005683724667
0.4606429636478424, [1,   401] loss: 0.52638116638708
0.48914235830307007, [1,   501] loss: 0.5157309139143683
0.4411412179470062, [1,   601] loss: 0.504374006945956
0.5176326632499695, [1,   701] loss: 0.49897487208608554
0.27043047547340393, [1,   801] loss: 0.4934909021465594
0.5001043677330017, [1,   901] loss: 0.4882685973378235
0.5260560512542725, [1,  1001] loss: 0.4853727099226116
0.39882692694664, [1,  1101] loss: 0.4831160401763034
0.34445658326148987, [1,  1201] loss: 0.4799900838041323
0.41472363471984863, [1,  1301] loss: 0.47764215629396073
0.46200093626976013, [1,  1401] loss: 0.4764466583210281
0.4553074240684509, [1,  1501] loss: 0.4750267454571302
0.5308207273483276, [1,  1601] loss: 0.4735661609287954
0.2915763258934021, [1,  1701] loss: 0.47126892187261954
0.4983507990837097, [1,  1801] loss: 0.4704551

0.62673419713974, [1,   101] loss: 0.643911064851402
0.4814194142818451, [1,   201] loss: 0.5934478357360138
0.5690101385116577, [1,   301] loss: 0.5530582879270826
0.47456055879592896, [1,   401] loss: 0.5285919158536002
0.4356340765953064, [1,   501] loss: 0.5163762314233952
0.5658431649208069, [1,   601] loss: 0.5070892662157036
0.2878817021846771, [1,   701] loss: 0.49775964859208777
0.5520589351654053, [1,   801] loss: 0.4944653199629837
0.5033761262893677, [1,   901] loss: 0.48932423923044704
0.33669519424438477, [1,  1001] loss: 0.48455131640443794
0.4373447895050049, [1,  1101] loss: 0.4812891424027061
0.49595576524734497, [1,  1201] loss: 0.4795798912433462
0.39214906096458435, [1,  1301] loss: 0.47657697946749494
0.5623655319213867, [1,  1401] loss: 0.4754501318001985
0.5169384479522705, [1,  1501] loss: 0.47411441322984416
0.4832735061645508, [1,  1601] loss: 0.47333435767762444
0.5066928863525391, [1,  1701] loss: 0.47202972749325894
0.3948180675506592, [1,  1801] loss: 0.4

0.5960143208503723, [1,   101] loss: 0.6408954451579859
0.5155699253082275, [1,   201] loss: 0.5876600258979038
0.3581860661506653, [1,   301] loss: 0.5488233052416893
0.5046767592430115, [1,   401] loss: 0.5259366308959048
0.5071157217025757, [1,   501] loss: 0.512145689534332
0.5000525712966919, [1,   601] loss: 0.5050821508871338
0.4588409960269928, [1,   701] loss: 0.4976134196072604
0.49650758504867554, [1,   801] loss: 0.4917980588405171
0.5397152900695801, [1,   901] loss: 0.4871012045692789
0.2629404664039612, [1,  1001] loss: 0.48341580236202236
0.42707446217536926, [1,  1101] loss: 0.48139515534029775
0.3398429751396179, [1,  1201] loss: 0.47868538033108626
0.4132043123245239, [1,  1301] loss: 0.47602715702307946
0.408808171749115, [1,  1401] loss: 0.47417623475778964
0.32976460456848145, [1,  1501] loss: 0.47294412497716454
0.5317829251289368, [1,  1601] loss: 0.4721894353572314
0.4475173056125641, [1,  1701] loss: 0.4709548870915178
0.4801507592201233, [1,  1801] loss: 0.46

0.5388966798782349, [1,   101] loss: 0.6378732016771147
0.4282650053501129, [1,   201] loss: 0.5896434949998238
0.537812352180481, [1,   301] loss: 0.5514270233058454
0.4595404863357544, [1,   401] loss: 0.5255918018612779
0.49033886194229126, [1,   501] loss: 0.5119675336305253
0.30539608001708984, [1,   601] loss: 0.5010496658860348
0.5630233883857727, [1,   701] loss: 0.4940717924125865
0.5475245714187622, [1,   801] loss: 0.4881116863009933
0.503110408782959, [1,   901] loss: 0.483587533764781
0.3754557967185974, [1,  1001] loss: 0.4806025133325861
0.5454958081245422, [1,  1101] loss: 0.4783942499396803
0.4324403703212738, [1,  1201] loss: 0.4760229574899491
0.426386296749115, [1,  1301] loss: 0.4737765041225054
0.23378205299377441, [1,  1401] loss: 0.4717281125725209
0.40958213806152344, [1,  1501] loss: 0.47079806324643025
0.48910409212112427, [1,  1601] loss: 0.46902583415697396
0.5074963569641113, [1,  1701] loss: 0.46834560697881844
0.4394890367984772, [1,  1801] loss: 0.46722

0.5972872972488403, [1,   101] loss: 0.6452266656526244
0.5190293192863464, [1,   201] loss: 0.5936797981831565
0.404377281665802, [1,   301] loss: 0.551898123616
0.5221261978149414, [1,   401] loss: 0.5310311899369494
0.5601124167442322, [1,   501] loss: 0.520501543364363
0.4947899281978607, [1,   601] loss: 0.511724368655146
0.45258551836013794, [1,   701] loss: 0.5031272198436264
0.45328032970428467, [1,   801] loss: 0.497061267085885
0.4578026235103607, [1,   901] loss: 0.4919466799689451
0.49258625507354736, [1,  1001] loss: 0.4872873306988955
0.47545960545539856, [1,  1101] loss: 0.4857293321910931
0.4608650803565979, [1,  1201] loss: 0.4816606381255125
0.5705342292785645, [1,  1301] loss: 0.48019019992510964
0.5169204473495483, [1,  1401] loss: 0.4774698382888327
0.435808002948761, [1,  1501] loss: 0.47488844326680535
0.41995343565940857, [1,  1601] loss: 0.47347038520324386
0.4433448314666748, [1,  1701] loss: 0.4711474313946558
0.5267219543457031, [1,  1801] loss: 0.4706001349

## Language Families

We continue the Leave One Out approach, but instead of training on all other languages, we train only on other languages within the same language family. The Train sets are naturally smaller here than in the All Languages or LOO datasets, since there are only one or two languages used in the Train set.

In [ ]:
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Original', 'All_Langs_Test_Original.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Train_Original.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Val_Original.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_FNN_Original'
    family_fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

    # Train model and log on wandb
    family_fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

    # Save model to Drive
    torch.save(family_fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_fnn_model.predict(test_dl, separate_words=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

wandb: Currently logged in as: linguistics-log. Use `wandb login --relogin` to force relogin


0.5620887875556946, [1,   101] loss: 0.6758249785640452
0.4158664643764496, [1,   201] loss: 0.6000916303242024
0.5875289440155029, [1,   301] loss: 0.5501696376804498
0.42462193965911865, [1,   401] loss: 0.5239666677695557
0.4701705873012543, [1,   501] loss: 0.5059905461446492
0.47905388474464417, [1,   601] loss: 0.4927373299880353
0.3964865505695343, [1,   701] loss: 0.48393425441077365
0.40768131613731384, [1,   801] loss: 0.4776265470871467
0.34001293778419495, [1,   901] loss: 0.4716512066013408
0.3300480842590332, [1,  1001] loss: 0.4663450399955193
0.40523210167884827, [1,  1101] loss: 0.4634091474325629
0.4516841173171997, [1,  1201] loss: 0.46162481381434584

Validation Loss
tensor(0.4429)

0.39171016216278076, [1,   101] loss: 0.42899875814961913
0.4402872323989868, [1,   201] loss: 0.42627637310704186
0.3554377555847168, [1,   301] loss: 0.4259757414905732
0.4184882640838623, [1,   401] loss: 0.423594830525189
0.43557050824165344, [1,   501] loss: 0.4229511044874877
0.468

0.600806474685669, [1,   101] loss: 0.6753944140849727
0.5167028903961182, [1,   201] loss: 0.5948864636729606
0.368290513753891, [1,   301] loss: 0.5477386575402612
0.29300013184547424, [1,   401] loss: 0.5206726957437701
0.40090665221214294, [1,   501] loss: 0.5060339424305571
0.4493963420391083, [1,   601] loss: 0.494683451987741
0.4018348157405853, [1,   701] loss: 0.4862756638145991
0.38013333082199097, [1,   801] loss: 0.4791496484057882
0.4587166905403137, [1,   901] loss: 0.47430788083095
0.39569807052612305, [1,  1001] loss: 0.470723621807732
0.39184078574180603, [1,  1101] loss: 0.4668009576339488
0.4681699275970459, [1,  1201] loss: 0.46387483447566813
0.5006572604179382, [1,  1301] loss: 0.46129903477902234
0.4009936451911926, [1,  1401] loss: 0.4591956950250819
0.5203486084938049, [1,  1501] loss: 0.4572346408334595
0.4273110330104828, [1,  1601] loss: 0.4551265622901589
0.41082021594047546, [1,  1701] loss: 0.4538294245378891
0.4316416382789612, [1,  1801] loss: 0.4522911

0.6212824583053589, [1,   101] loss: 0.6789446567544842
0.4776746332645416, [1,   201] loss: 0.6083174663693157
0.4495774805545807, [1,   301] loss: 0.5573543726259291
0.52735435962677, [1,   401] loss: 0.5266624438086352
0.4641517996788025, [1,   501] loss: 0.5094658096661111
0.45931312441825867, [1,   601] loss: 0.4980127312205794
0.506369948387146, [1,   701] loss: 0.49018610630200354
0.4131929874420166, [1,   801] loss: 0.4838682482026043
0.40452903509140015, [1,   901] loss: 0.4782205460785364
0.49293622374534607, [1,  1001] loss: 0.47317181339303216
0.5056273341178894, [1,  1101] loss: 0.469814540370013
0.4110865294933319, [1,  1201] loss: 0.46675903780647954
0.48200398683547974, [1,  1301] loss: 0.4635453479082469
0.5780178904533386, [1,  1401] loss: 0.46057315022391476
0.5184918642044067, [1,  1501] loss: 0.45865212975046304
0.44267138838768005, [1,  1601] loss: 0.4568458428975197
0.40980979800224304, [1,  1701] loss: 0.45466621436051663
0.4652256369590759, [1,  1801] loss: 0.4

0.6350698471069336, [1,   101] loss: 0.6813353648280153
0.5263729095458984, [1,   201] loss: 0.6110044019435769
0.5912908315658569, [1,   301] loss: 0.5807320057751728
0.5133813619613647, [1,   401] loss: 0.5661292345149261
0.6053351163864136, [1,   501] loss: 0.5556606459998323
0.5139102935791016, [1,   601] loss: 0.5477035269761046
0.5683901906013489, [1,   701] loss: 0.5420428573149927
0.5407328009605408, [1,   801] loss: 0.5395390662212348
0.533184289932251, [1,   901] loss: 0.5360424730443002

Validation Loss
tensor(0.5055)

0.44609349966049194, [1,   101] loss: 0.5157014833818568
0.5391092300415039, [1,   201] loss: 0.514744013399627
0.5764598846435547, [1,   301] loss: 0.5155503031027278
0.5585113763809204, [1,   401] loss: 0.51419722751489
0.4758453667163849, [1,   501] loss: 0.5123501362914811
0.5189687013626099, [1,   601] loss: 0.5105480466428494
0.49177512526512146, [1,   701] loss: 0.5096331718304699
0.5668118000030518, [1,   801] loss: 0.5086463097385253
0.504203379154205

0.598229169845581, [1,   101] loss: 0.6764145776776984
0.4962722063064575, [1,   201] loss: 0.5992054486304373
0.4837947487831116, [1,   301] loss: 0.5668931565312452
0.46123048663139343, [1,   401] loss: 0.5485088550613408
0.5931090712547302, [1,   501] loss: 0.5372571316129433
0.5371087193489075, [1,   601] loss: 0.5295911655201888
0.48427891731262207, [1,   701] loss: 0.524658114483285
0.5584247708320618, [1,   801] loss: 0.5209506146991149
0.47543853521347046, [1,   901] loss: 0.5164788171863979

Validation Loss
tensor(0.5425)

0.5099701285362244, [1,   101] loss: 0.48446115541576157
0.44771668314933777, [1,   201] loss: 0.4771360671194039
0.4787862300872803, [1,   301] loss: 0.4765449263823785
0.3062164783477783, [1,   401] loss: 0.4761714456681896
0.4278990924358368, [1,   501] loss: 0.47854961172311367
0.599220871925354, [1,   601] loss: 0.4806519932734986
0.43639129400253296, [1,   701] loss: 0.48144502408494283
0.5775560140609741, [1,   801] loss: 0.48251172037011525
0.3346401

0.6204572319984436, [1,   101] loss: 0.676495632912853
0.4032217860221863, [1,   201] loss: 0.6077989534062532
0.48155492544174194, [1,   301] loss: 0.5778764407104036
0.4738233685493469, [1,   401] loss: 0.5630416210898734
0.38134080171585083, [1,   501] loss: 0.554288083267307
0.5023072361946106, [1,   601] loss: 0.5484074965590446
0.5453009009361267, [1,   701] loss: 0.5404299280782909
0.4496847093105316, [1,   801] loss: 0.5340571367227183
0.5737650990486145, [1,   901] loss: 0.5298574226975573
0.44957995414733887, [1,  1001] loss: 0.5265137266654235
0.4097289741039276, [1,  1101] loss: 0.5240507452096537

Validation Loss
tensor(0.5235)

0.4670785665512085, [1,   101] loss: 0.4851507320262418
0.6227380633354187, [1,   201] loss: 0.4847227226738906
0.4802101254463196, [1,   301] loss: 0.4929393945738327
0.4595373570919037, [1,   401] loss: 0.49184006868752456
0.4479994773864746, [1,   501] loss: 0.4906270637245711
0.5070815682411194, [1,   601] loss: 0.49131674159584743
0.5553000569

0.6275129914283752, [1,   101] loss: 0.6753899608508195
0.4549490511417389, [1,   201] loss: 0.5919279602926169
0.4784027934074402, [1,   301] loss: 0.5462490477633238
0.46069735288619995, [1,   401] loss: 0.5204746873301461
0.4410666823387146, [1,   501] loss: 0.5039457355787654
0.36882299184799194, [1,   601] loss: 0.49100675013616757
0.4130007326602936, [1,   701] loss: 0.48249011776926853
0.5087348222732544, [1,   801] loss: 0.4762615046920848
0.3745816946029663, [1,   901] loss: 0.47037098775891695
0.4616769254207611, [1,  1001] loss: 0.46650537183056107
0.4294101595878601, [1,  1101] loss: 0.46268701649437594
0.37655624747276306, [1,  1201] loss: 0.4593611920033764
0.5580747723579407, [1,  1301] loss: 0.45642257177719786

Validation Loss
tensor(0.4454)

0.4079161584377289, [1,   101] loss: 0.4189935642303807
0.44927793741226196, [1,   201] loss: 0.4147733504054558
0.44541028141975403, [1,   301] loss: 0.4181358239480427
0.3534619212150574, [1,   401] loss: 0.4186590278609435
0.36

0.636557936668396, [1,   101] loss: 0.6776517051281316
0.4870029091835022, [1,   201] loss: 0.601363667801245
0.4112357795238495, [1,   301] loss: 0.5532868220362552
0.4815562069416046, [1,   401] loss: 0.5304311898135188
0.5456479787826538, [1,   501] loss: 0.5163037343891319
0.42473527789115906, [1,   601] loss: 0.506096690992349
0.5172227621078491, [1,   701] loss: 0.49800742535550313
0.3691117763519287, [1,   801] loss: 0.4909937317563353
0.4356539249420166, [1,   901] loss: 0.4854862263114021

Validation Loss
tensor(0.4333)

0.4012744426727295, [1,   101] loss: 0.4480872847656212
0.472513347864151, [1,   201] loss: 0.44649099339893206
0.5329422354698181, [1,   301] loss: 0.4439707850895055
0.4926663041114807, [1,   401] loss: 0.44254150321507396
0.5167465209960938, [1,   501] loss: 0.4412402371743958
0.45317795872688293, [1,   601] loss: 0.4418966269086482
0.44883519411087036, [1,   701] loss: 0.442212192695083
0.37982726097106934, [1,   801] loss: 0.44252789502361145
0.4089066684

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Train_Original.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Val_Original.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_CNN_Original'
    family_cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

    # Train model and log on wandb
    family_cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

    # Save model to Drive
    torch.save(family_cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_cnn_model.predict(test_dl, separate_words=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5140825510025024, [1,   101] loss: 0.6405402162287495
0.35523635149002075, [1,   201] loss: 0.5504997774439665
0.552558183670044, [1,   301] loss: 0.5031586503269665
0.4105726182460785, [1,   401] loss: 0.47950638815797775
0.46543675661087036, [1,   501] loss: 0.46390050608002975
0.4460887014865875, [1,   601] loss: 0.45079448157162116
0.3106786906719208, [1,   701] loss: 0.44227585755554316
0.32231786847114563, [1,   801] loss: 0.4369144183531236
0.2777552604675293, [1,   901] loss: 0.4305826637162088
0.24346648156642914, [1,  1001] loss: 0.4254709276911262
0.315805584192276, [1,  1101] loss: 0.42301031959993424
0.35923880338668823, [1,  1201] loss: 0.4222044240525124

Validation Loss
tensor(0.4366)

0.344410240650177, [1,   101] loss: 0.39804870318068136
0.4266641139984131, [1,   201] loss: 0.3855617591249409
0.2659767270088196, [1,   301] loss: 0.38312743599232646
0.3733009397983551, [1,   401] loss: 0.37559042575576357
0.38993340730667114, [1,   501] loss: 0.3707007846075618
0.38

0.5153381824493408, [1,   101] loss: 0.6388002628147011
0.5223511457443237, [1,   201] loss: 0.5543396865847099
0.2583557665348053, [1,   301] loss: 0.5150449481913417
0.24686689674854279, [1,   401] loss: 0.49349168344328825
0.2948992848396301, [1,   501] loss: 0.4822463001498205
0.450868159532547, [1,   601] loss: 0.47218327397812226
0.35808584094047546, [1,   701] loss: 0.46608212420161543
0.3964032828807831, [1,   801] loss: 0.45955602462855766
0.4616471230983734, [1,   901] loss: 0.45510860378714435
0.35166019201278687, [1,  1001] loss: 0.45164512949330465
0.3708357512950897, [1,  1101] loss: 0.44697238114424775
0.4428423345088959, [1,  1201] loss: 0.4423107647156338
0.4354773163795471, [1,  1301] loss: 0.43758643354982896
0.35523363947868347, [1,  1401] loss: 0.4331876157671958
0.4502454698085785, [1,  1501] loss: 0.42855479428761806
0.36936530470848083, [1,  1601] loss: 0.4239466476122116
0.3530307114124298, [1,  1701] loss: 0.42059619620941724
0.3982131779193878, [1,  1801] los

0.5562058687210083, [1,   101] loss: 0.6468581958572464
0.47972413897514343, [1,   201] loss: 0.568381423677378
0.44309306144714355, [1,   301] loss: 0.523676485021249
0.5137104988098145, [1,   401] loss: 0.49498013838047994
0.4596957266330719, [1,   501] loss: 0.47874410017700253
0.4592255651950836, [1,   601] loss: 0.46834181520635393
0.5221496820449829, [1,   701] loss: 0.4610705304885557
0.35663121938705444, [1,   801] loss: 0.45496582165453464
0.34610849618911743, [1,   901] loss: 0.4487827018225828
0.4736745357513428, [1,  1001] loss: 0.44302004823958
0.4760015904903412, [1,  1101] loss: 0.43826789528023213
0.3831826150417328, [1,  1201] loss: 0.43413519029265935
0.44466540217399597, [1,  1301] loss: 0.42939513038663474
0.5194448828697205, [1,  1401] loss: 0.4246932057787443
0.4533764123916626, [1,  1501] loss: 0.4214449008377015
0.37391671538352966, [1,  1601] loss: 0.41845025416512477
0.39401957392692566, [1,  1701] loss: 0.41503471773619305
0.40992558002471924, [1,  1801] loss

0.5009968876838684, [1,   101] loss: 0.640956576802943
0.4152544438838959, [1,   201] loss: 0.5384710424426776
0.49250665307044983, [1,   301] loss: 0.5072047254967927
0.395508348941803, [1,   401] loss: 0.48979912761440897
0.5156475901603699, [1,   501] loss: 0.477815978660317
0.4352133870124817, [1,   601] loss: 0.4672605842599853
0.48683395981788635, [1,   701] loss: 0.46108146449723697
0.4574451446533203, [1,   801] loss: 0.4573097682921925
0.43936604261398315, [1,   901] loss: 0.4527665796409569

Validation Loss
tensor(0.5050)

0.33331888914108276, [1,   101] loss: 0.41908132970923245
0.4272282123565674, [1,   201] loss: 0.4165079013921728
0.4557068347930908, [1,   301] loss: 0.4178907696491856
0.42107832431793213, [1,   401] loss: 0.41609818813509475
0.37947896122932434, [1,   501] loss: 0.4148657255008549
0.437518447637558, [1,   601] loss: 0.41283335974331503
0.3902318477630615, [1,   701] loss: 0.41156197712356796
0.4583086669445038, [1,   801] loss: 0.4101264415199539
0.40621

0.50225430727005, [1,   101] loss: 0.6381248822896788
0.4240879416465759, [1,   201] loss: 0.5581003512019542
0.4319567084312439, [1,   301] loss: 0.5254396263547118
0.4052896499633789, [1,   401] loss: 0.5049187591173999
0.5562043190002441, [1,   501] loss: 0.4926257778606015
0.4917006194591522, [1,   601] loss: 0.4839966824516877
0.4448939859867096, [1,   701] loss: 0.47824228264805935
0.5111014246940613, [1,   801] loss: 0.47399307872993074
0.42475923895835876, [1,   901] loss: 0.46845056159580983

Validation Loss
tensor(0.4737)

0.46425166726112366, [1,   101] loss: 0.43281329401058727
0.3897710144519806, [1,   201] loss: 0.4246429803581973
0.4354400038719177, [1,   301] loss: 0.42318768168109594
0.2595352828502655, [1,   401] loss: 0.4223071184204404
0.36175522208213806, [1,   501] loss: 0.42420273512125967
0.5235671401023865, [1,   601] loss: 0.4262875410636729
0.3800782859325409, [1,   701] loss: 0.4264926045133962
0.5053181648254395, [1,   801] loss: 0.427102737165941
0.2354045

0.5369387865066528, [1,   101] loss: 0.6542028436566344
0.28675752878189087, [1,   201] loss: 0.561531330667325
0.4514237940311432, [1,   301] loss: 0.5245146869226943
0.39808258414268494, [1,   401] loss: 0.5059443889116111
0.25654566287994385, [1,   501] loss: 0.4943332016289591
0.4254305958747864, [1,   601] loss: 0.4868381672264534
0.46241217851638794, [1,   701] loss: 0.4774743803855186
0.4318515658378601, [1,   801] loss: 0.470182950632849
0.47974470257759094, [1,   901] loss: 0.4649417334040844
0.35220804810523987, [1,  1001] loss: 0.4609045396437059
0.352037250995636, [1,  1101] loss: 0.4578483149571705

Validation Loss
tensor(0.4642)

0.4333558678627014, [1,   101] loss: 0.40865716884041775
0.5087502598762512, [1,   201] loss: 0.4098596414968149
0.4006311297416687, [1,   301] loss: 0.41778588621719337
0.4185120165348053, [1,   401] loss: 0.41621868932930906
0.3624208867549896, [1,   501] loss: 0.41530418859984347
0.43546149134635925, [1,   601] loss: 0.4151085433418461
0.46861

0.5932607650756836, [1,   101] loss: 0.6413948636243839
0.49797624349594116, [1,   201] loss: 0.5639928469610451
0.5308547616004944, [1,   301] loss: 0.5317474224440679
0.5018142461776733, [1,   401] loss: 0.5102387318141443
0.44524243474006653, [1,   501] loss: 0.49685201569350657
0.3888227939605713, [1,   601] loss: 0.4851460139237704
0.4105217158794403, [1,   701] loss: 0.4757015773981342
0.4633908271789551, [1,   801] loss: 0.46586565971002447
0.3028410077095032, [1,   901] loss: 0.45628124926152425
0.41870826482772827, [1,  1001] loss: 0.44919562866756846
0.4189908504486084, [1,  1101] loss: 0.44236108151811776
0.309840589761734, [1,  1201] loss: 0.4363697456206807
0.5134196281433105, [1,  1301] loss: 0.43086732296898766

Validation Loss
tensor(0.3968)

0.3686801791191101, [1,   101] loss: 0.3643159864857645
0.3890174627304077, [1,   201] loss: 0.36012738961633756
0.3912378251552582, [1,   301] loss: 0.3646484400792375
0.2647661566734314, [1,   401] loss: 0.3651761645056363
0.2837

0.5815424919128418, [1,   101] loss: 0.6437599641261714
0.4840277135372162, [1,   201] loss: 0.565975929670666
0.41320106387138367, [1,   301] loss: 0.5241498111985451
0.47946038842201233, [1,   401] loss: 0.5055007955008314
0.5454626083374023, [1,   501] loss: 0.49209216727824984
0.4198291003704071, [1,   601] loss: 0.4825963733993632
0.5222543478012085, [1,   701] loss: 0.4747732612975314
0.30781328678131104, [1,   801] loss: 0.4681602908337905
0.4383541941642761, [1,   901] loss: 0.462691178754154

Validation Loss
tensor(0.4329)

0.3432729244232178, [1,   101] loss: 0.4260843648473815
0.4624400734901428, [1,   201] loss: 0.42567976834762156
0.5215328335762024, [1,   301] loss: 0.4199328277742744
0.47186893224716187, [1,   401] loss: 0.4166271688969355
0.48954296112060547, [1,   501] loss: 0.41177863328756686
0.39724618196487427, [1,   601] loss: 0.4110382662810224
0.4244902729988098, [1,   701] loss: 0.4100741723315862
0.3267958164215088, [1,   801] loss: 0.40867684540639954
0.37844

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Original/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Original/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Train_Original.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Original', 'Family', f'{family[0]}_{lang[1]}_Val_Original.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_LSTM_Original'
    family_lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

    # Train model and log on wandb
    family_lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

    # Save model to Drive
    torch.save(family_lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_lstm_model.predict(test_dl, separate_words=True, lstm=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.48557090759277344, [1,   101] loss: 0.6247277802760058
0.43572354316711426, [1,   201] loss: 0.5660585953821591
0.5579293370246887, [1,   301] loss: 0.5221038635981043
0.4179411828517914, [1,   401] loss: 0.49567162942262066
0.4725983142852783, [1,   501] loss: 0.47769609022283266
0.4586947560310364, [1,   601] loss: 0.46384216403703327
0.3149026334285736, [1,   701] loss: 0.45405197594203217
0.33547502756118774, [1,   801] loss: 0.447585517854503
0.2717147469520569, [1,   901] loss: 0.4402535229044802
0.24463704228401184, [1,  1001] loss: 0.4343807989550935
0.32916486263275146, [1,  1101] loss: 0.43152806190240933
0.36334678530693054, [1,  1201] loss: 0.4303568984528416

Validation Loss
tensor(0.4424)

0.3673129975795746, [1,   101] loss: 0.40619104141646095
0.4422401189804077, [1,   201] loss: 0.39611632021060633
0.26225006580352783, [1,   301] loss: 0.39723028405956257
0.429211288690567, [1,   401] loss: 0.39425511431515664
0.423406183719635, [1,   501] loss: 0.39316591655393085
0

0.5564770102500916, [1,   101] loss: 0.6329472495777773
0.5466372966766357, [1,   201] loss: 0.5858256544046734
0.282719224691391, [1,   301] loss: 0.5465034073175385
0.15973298251628876, [1,   401] loss: 0.5191436060460428
0.3157167136669159, [1,   501] loss: 0.5047664420154994
0.4537661075592041, [1,   601] loss: 0.49244509384457563
0.3711715638637543, [1,   701] loss: 0.484994966318876
0.4188050925731659, [1,   801] loss: 0.47752295960015273
0.4650629162788391, [1,   901] loss: 0.47236486036458636
0.3901959955692291, [1,  1001] loss: 0.4683046635095175
0.4128390848636627, [1,  1101] loss: 0.46395498173790123
0.4920278489589691, [1,  1201] loss: 0.46098684690750014
0.5001651048660278, [1,  1301] loss: 0.4583040889607403
0.4120478332042694, [1,  1401] loss: 0.45639146587344087
0.5135687589645386, [1,  1501] loss: 0.4539261038931984
0.4629771411418915, [1,  1601] loss: 0.4513262233171591
0.39054688811302185, [1,  1701] loss: 0.4499792353475115
0.4427548944950104, [1,  1801] loss: 0.447

0.5765799283981323, [1,   101] loss: 0.6360758531211627
0.517681360244751, [1,   201] loss: 0.5938526009445759
0.4703986644744873, [1,   301] loss: 0.5505796120412326
0.5174667239189148, [1,   401] loss: 0.5176855030276829
0.4731653034687042, [1,   501] loss: 0.4990864233327602
0.46871063113212585, [1,   601] loss: 0.487073620418691
0.5241689085960388, [1,   701] loss: 0.4784297085873326
0.36958047747612, [1,   801] loss: 0.47143891820691053
0.3631826341152191, [1,   901] loss: 0.46501738006263543
0.4999927282333374, [1,  1001] loss: 0.45904644019343516
0.5214060544967651, [1,  1101] loss: 0.45508801713450514
0.3948074281215668, [1,  1201] loss: 0.4520427217485258
0.4896487593650818, [1,  1301] loss: 0.4484135116114754
0.5522444248199463, [1,  1401] loss: 0.4449832975275437
0.5210913419723511, [1,  1501] loss: 0.4428220873954225
0.4601876437664032, [1,  1601] loss: 0.44136377517599323
0.415191650390625, [1,  1701] loss: 0.43891788167448637
0.45444127917289734, [1,  1801] loss: 0.436884

0.6302610039710999, [1,   101] loss: 0.6594759107816337
0.43853285908699036, [1,   201] loss: 0.5888418358060258
0.5088755488395691, [1,   301] loss: 0.5423032832749658
0.41269850730895996, [1,   401] loss: 0.5180987807692138
0.5244616270065308, [1,   501] loss: 0.5023444763230468
0.451493501663208, [1,   601] loss: 0.4895535238744217
0.4857085645198822, [1,   701] loss: 0.48210557035772333
0.48230230808258057, [1,   801] loss: 0.47770722501547297
0.46455222368240356, [1,   901] loss: 0.472656795281615

Validation Loss
tensor(0.4788)

0.35841822624206543, [1,   101] loss: 0.4404017341018903
0.4238702952861786, [1,   201] loss: 0.4384766825989111
0.4991488754749298, [1,   301] loss: 0.4402013529475741
0.44552645087242126, [1,   401] loss: 0.4384605761552392
0.416542649269104, [1,   501] loss: 0.43630431131450476
0.46879827976226807, [1,   601] loss: 0.4337390756944253
0.3861231803894043, [1,   701] loss: 0.43246521308656766
0.49687162041664124, [1,   801] loss: 0.430948049764843
0.42825

0.569110631942749, [1,   101] loss: 0.6342267246529607
0.446796715259552, [1,   201] loss: 0.573317534776766
0.4380471706390381, [1,   301] loss: 0.5376941801553152
0.3993089497089386, [1,   401] loss: 0.5156894955886272
0.5548282861709595, [1,   501] loss: 0.5029981719430335
0.5067079663276672, [1,   601] loss: 0.49467391270319755
0.4644692540168762, [1,   701] loss: 0.48910658603558016
0.5426056981086731, [1,   801] loss: 0.4854970612282982
0.44013503193855286, [1,   901] loss: 0.4806409130838351

Validation Loss
tensor(0.4703)

0.4490433931350708, [1,   101] loss: 0.44917151110597175
0.43210935592651367, [1,   201] loss: 0.4406841100188927
0.4459574222564697, [1,   301] loss: 0.44033403240416535
0.25965774059295654, [1,   401] loss: 0.4395944933567261
0.37952080368995667, [1,   501] loss: 0.44246389429845256
0.5571482181549072, [1,   601] loss: 0.44510820103861926
0.3792846202850342, [1,   701] loss: 0.44586095891988564
0.5404855608940125, [1,   801] loss: 0.44671862221761294
0.2335

0.5713404417037964, [1,   101] loss: 0.6388090046325533
0.3172306418418884, [1,   201] loss: 0.5797570563519179
0.4609962999820709, [1,   301] loss: 0.5418778000974972
0.41105586290359497, [1,   401] loss: 0.5209691931407647
0.2647748589515686, [1,   501] loss: 0.5081364267957424
0.4535723030567169, [1,   601] loss: 0.5001627078369731
0.4563273787498474, [1,   701] loss: 0.4906437397640884
0.44912371039390564, [1,   801] loss: 0.4830260698947493
0.5001711249351501, [1,   901] loss: 0.4777578996343499
0.3778231143951416, [1,  1001] loss: 0.4739079486158166
0.3842119872570038, [1,  1101] loss: 0.47106565091146546

Validation Loss
tensor(0.4738)

0.421109139919281, [1,   101] loss: 0.4290994250833398
0.5605794787406921, [1,   201] loss: 0.42965850790045157
0.429718017578125, [1,   301] loss: 0.4375735654981429
0.3750782012939453, [1,   401] loss: 0.43599614173991424
0.37704572081565857, [1,   501] loss: 0.4350015601950015
0.4593389630317688, [1,   601] loss: 0.4348474322708197
0.478923797

0.6155282855033875, [1,   101] loss: 0.6368608911438743
0.529939591884613, [1,   201] loss: 0.5911930465876166
0.5425208210945129, [1,   301] loss: 0.5581109153471911
0.5200465321540833, [1,   401] loss: 0.5337901871995141
0.45054206252098083, [1,   501] loss: 0.5183629252001672
0.4326479136943817, [1,   601] loss: 0.5065970319430165
0.45854344964027405, [1,   701] loss: 0.4987080019610414
0.5500045418739319, [1,   801] loss: 0.49374340506230996
0.3313394784927368, [1,   901] loss: 0.4881525505313466
0.5097267627716064, [1,  1001] loss: 0.4854367686050398
0.3914972245693207, [1,  1101] loss: 0.4820509003500685
0.34934893250465393, [1,  1201] loss: 0.47920057238649566
0.5698643922805786, [1,  1301] loss: 0.47597051143566066

Validation Loss
tensor(0.4420)

0.49191558361053467, [1,   101] loss: 0.44048329346840925
0.43167367577552795, [1,   201] loss: 0.43567155695413773
0.5108509063720703, [1,   301] loss: 0.44146097820883373
0.3298805356025696, [1,   401] loss: 0.44315816938152486
0.33

0.5968666672706604, [1,   101] loss: 0.6347794845552728
0.5192903280258179, [1,   201] loss: 0.5875409249939135
0.4305118918418884, [1,   301] loss: 0.5427559974581696
0.48450300097465515, [1,   401] loss: 0.5222689145966956
0.5507767200469971, [1,   501] loss: 0.5084175151622224
0.4348118305206299, [1,   601] loss: 0.4990626784311158
0.5355575084686279, [1,   701] loss: 0.4913256336189541
0.2826486825942993, [1,   801] loss: 0.48403974900605823
0.4610951840877533, [1,   901] loss: 0.47807312309411204

Validation Loss
tensor(0.4436)

0.33984172344207764, [1,   101] loss: 0.43586732174205306
0.4695504307746887, [1,   201] loss: 0.4357969522550331
0.5322171449661255, [1,   301] loss: 0.4316777789414523
0.5179793834686279, [1,   401] loss: 0.42965732763830267
0.522213876247406, [1,   501] loss: 0.4268962411421859
0.45286858081817627, [1,   601] loss: 0.42886241166519246
0.4910258948802948, [1,   701] loss: 0.43003126493683047
0.34930750727653503, [1,   801] loss: 0.43104468002803764
0.435

# Train Models on Uniform Size Datasets

To give all languages equal representation in the Train and Test datasets, we sample them down to a uniform size. For the All Languages dataset we sample 12,000 words per language (total = 144,000) for Train and 1,500 words per language (total = 18,000) for Val and Test. For the LOO dataset we sample 13,091 words per language (total = 144,001) for Train, and use the remaining language for Val (13,500 words) and Test (1,500 words).

All words in the Uniform Size Test set were sampled exclusively from the Original Size Test set, so models trained on either Original Size datasets or Uniform Size datasets can be tested on the other's Test set without concern for data leakage.

## All Languages

In [ ]:
# Train and Val Datasets for All Languages
with open(os.path.join(data_folder, 'Uniform', 'All_Langs_Train_Uniform.pickle'), 'rb') as f:
  train_ds = pickle.load(f)
with open(os.path.join(data_folder, 'Uniform', 'All_Langs_Val_Uniform.pickle'), 'rb') as f:
  val_ds = pickle.load(f)
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Uniform', 'All_Langs_Test_Uniform.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

### FNN

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

# Train model and log on wandb
fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

# Save model to Drive
torch.save(fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.656072735786438, [1,   101] loss: 0.678664213950091
0.536149799823761, [1,   201] loss: 0.6084985036162002
0.5434888601303101, [1,   301] loss: 0.5709536419160343
0.44798144698143005, [1,   401] loss: 0.5473901973549564
0.48263198137283325, [1,   501] loss: 0.5351088818259344
0.4803045690059662, [1,   601] loss: 0.5258765570484659
0.48163169622421265, [1,   701] loss: 0.5193626806458801
0.4341212213039398, [1,   801] loss: 0.5133971650241763
0.5222148299217224, [1,   901] loss: 0.5098192695441441
0.5082156658172607, [1,  1001] loss: 0.5064974536488464
0.5558537840843201, [1,  1101] loss: 0.5049212804769625
0.48616236448287964, [1,  1201] loss: 0.50187414023501
0.5038561224937439, [1,  1301] loss: 0.4999978617921781
0.4945763349533081, [1,  1401] loss: 0.4978754101141617
0.4850175380706787, [1,  1501] loss: 0.49647338388563395
0.43338653445243835, [1,  1601] loss: 0.49553599191374664
0.49145013093948364, [1,  1701] loss: 0.4941978267558808
0.48720043897628784, [1,  1801] loss: 0.49276

In [ ]:
#@title Load FNN
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)
fnn_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

In [ ]:
#@title Evaluate FNN

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = fnn_model.predict(test_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Uniform'
fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
fnn_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999991              1        tr             0          0        s
1     0.071968              0        tr             0          1        o
2     0.438129              1        tr             0          2        J
3     0.431931              0        tr             0          3        u
4     0.414869              0        tr             0          4        n
5     0.225846              1        tr             0          5        m
6     0.276902              0        tr             0          6        a
7     0.195307              0        tr             0          7        k
8     0.999981              1        el             1          0        e
9     0.147018              0        el             1          1        n

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_FNN_7gram_15hidden_5layers_10epochs_Uniform'
fnn_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
fnn_output[:10]

### CNN

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

# Train model and log on wandb
cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

# Save model to Drive
torch.save(cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.5867023468017578, [1,   101] loss: 0.6490506382271795
0.5167118906974792, [1,   201] loss: 0.562019622741054
0.5608123540878296, [1,   301] loss: 0.5304922811018669
0.38532209396362305, [1,   401] loss: 0.5090001408298711
0.48638486862182617, [1,   501] loss: 0.4993641564172661
0.4447479546070099, [1,   601] loss: 0.4913222971256085
0.4408446252346039, [1,   701] loss: 0.4858572806806945
0.4612256586551666, [1,   801] loss: 0.4800932750794176
0.5235835313796997, [1,   901] loss: 0.4772709253327828
0.47965049743652344, [1,  1001] loss: 0.4742455672878366
0.5098199844360352, [1,  1101] loss: 0.4721608361014445
0.45022091269493103, [1,  1201] loss: 0.46757738932433673
0.4628339409828186, [1,  1301] loss: 0.4645535963072766
0.44183430075645447, [1,  1401] loss: 0.46129125394964116
0.4384268522262573, [1,  1501] loss: 0.45916174500585
0.3774793744087219, [1,  1601] loss: 0.4573306155988457
0.4506920278072357, [1,  1701] loss: 0.45482794459972714
0.4411342442035675, [1,  1801] loss: 0.4526

In [ ]:
#@title Load CNN
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)
cnn_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

In [ ]:
#@title Evaluate CNN

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = cnn_model.predict(test_dl, separate_words=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Uniform'
cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_CNN_7gram_15hidden_10layers_10epochs_Uniform'
cnn_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
cnn_output[:10]

### LSTM

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

# Set random seeds
random.seed(seed)
np.random.seed(seed)
torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
torch.manual_seed(seed)

# Set samplers and DataLoaders
train_sampler = EqualLengthsBatchSampler(train_ds, batch_size, seed)
train_dl = DataLoader(train_ds, batch_sampler=train_sampler)
val_sampler = EqualLengthsBatchSampler(val_ds, batch_size, seed)
val_dl = DataLoader(val_ds, batch_sampler=val_sampler)

# Set up model
lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

# Train model and log on wandb
lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

# Save model to Drive
torch.save(lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

0.6103366017341614, [1,   101] loss: 0.6403235911142708
0.539979100227356, [1,   201] loss: 0.5858537350127946
0.5656628608703613, [1,   301] loss: 0.5517704603184893
0.3861258029937744, [1,   401] loss: 0.526568029809771
0.4893518090248108, [1,   501] loss: 0.5136606176039892
0.4492237865924835, [1,   601] loss: 0.5038296276588805
0.44511401653289795, [1,   701] loss: 0.4969040548346522
0.463615357875824, [1,   801] loss: 0.49018379691499897
0.5297613739967346, [1,   901] loss: 0.4864809001391789
0.5032721757888794, [1,  1001] loss: 0.48322843872643373
0.5373433828353882, [1,  1101] loss: 0.4818779939986921
0.48696595430374146, [1,  1201] loss: 0.47835347320664234
0.4917234778404236, [1,  1301] loss: 0.4767661007961615
0.5108177065849304, [1,  1401] loss: 0.4743782261241597
0.4676647186279297, [1,  1501] loss: 0.47317102189106913
0.38186541199684143, [1,  1601] loss: 0.47255195165372954
0.5074267983436584, [1,  1701] loss: 0.47090437240035726
0.4800402522087097, [1,  1801] loss: 0.469

In [ ]:
#@title Load LSTM
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Uniform'
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform'

lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)
lstm_model.load_state_dict(torch.load(os.path.join(model_folder, f'{model_name}.pt')))

In [ ]:
#@title Evaluate LSTM

# Run predictions on Test Dataloader
test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
preds, sylls = lstm_model.predict(test_dl, separate_words=True, lstm=True)

# Format predictions, ground truths, languages, word indices, positions, and segments
# to feed into Pandas DataFrame
new_preds = [entry for row in preds for entry in row.cpu().numpy()]
new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
sylls_check = [entry for row in test_ds for entry in row[1]]
new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
new_segments = [segment for entry in test_ds for segment in entry[3]]
for i in range(len(sylls_check)):
  assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                          'Positions':new_positions, 'Segments':new_segments})

model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Uniform'
lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)
lstm_output[:10]

Predictions  Ground Truths Languages  Word Indices  Positions Segments
0     0.999721              1        tr             0          0        s
1     0.130081              0        tr             0          1        o
2     0.587262              1        tr             0          2        J
3     0.249429              0        tr             0          3        u
4     0.304370              0        tr             0          4        n
5     0.569232              1        tr             0          5        m
6     0.296292              0        tr             0          6        a
7     0.010131              0        tr             0          7        k
8     0.999686              1        el             1          0        e
9     0.243540              0        el             1          1        n

In [ ]:
# Load test results from Drive
model_name = 'All_Langs_LSTM_15hidden_10layers_bidirectional_10epochs_Uniform'
lstm_output = pd.read_csv(os.path.join(preds_folder, f'{model_name}.csv'))
lstm_output[:10]

## Leave One Out (LOO)

In [ ]:
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Uniform', 'All_Langs_Test_Uniform.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_FNN_Uniform'
  loo_fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

  # Train model and log on wandb
  loo_fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

  # Save model to Drive
  torch.save(loo_fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_fnn_model.predict(test_dl, separate_words=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5622891187667847, [1,   101] loss: 0.6785944877284589
0.32698744535446167, [1,   201] loss: 0.5988551580639028
0.5397917628288269, [1,   301] loss: 0.5626036015360855
0.41977351903915405, [1,   401] loss: 0.5419596895538363
0.5134841203689575, [1,   501] loss: 0.5314975971887688
0.5168963670730591, [1,   601] loss: 0.5233558528187271
0.46179723739624023, [1,   701] loss: 0.5169988688660756
0.4396917223930359, [1,   801] loss: 0.511969641055656
0.5331147313117981, [1,   901] loss: 0.5075194967805214
0.4790861904621124, [1,  1001] loss: 0.5033454425655283
0.4164341390132904, [1,  1101] loss: 0.5002896036888447
0.49357616901397705, [1,  1201] loss: 0.49843200042434377
0.4989612400531769, [1,  1301] loss: 0.4965309426245737
0.5390580296516418, [1,  1401] loss: 0.49448839127804706
0.4925161302089691, [1,  1501] loss: 0.493524651520257
0.5626491904258728, [1,  1601] loss: 0.4919683762746331
0.4742426872253418, [1,  1701] loss: 0.4909153409840989
0.39186879992485046, [1,  1801] loss: 0.4901

0.6255375742912292, [1,   101] loss: 0.6784380963533232
0.4713672399520874, [1,   201] loss: 0.5955826567476662
0.562031626701355, [1,   301] loss: 0.5568150698247541
0.42945072054862976, [1,   401] loss: 0.5402770468644668
0.4948796331882477, [1,   501] loss: 0.5305939691806744
0.47003060579299927, [1,   601] loss: 0.5223695408930993
0.47501951456069946, [1,   701] loss: 0.5150092198445692
0.5168694257736206, [1,   801] loss: 0.5106042405304391
0.48187118768692017, [1,   901] loss: 0.5075105264964829
0.5642859935760498, [1,  1001] loss: 0.5040736560459499
0.48822981119155884, [1,  1101] loss: 0.5016032906687335
0.47895219922065735, [1,  1201] loss: 0.49950104577158216
0.5217342376708984, [1,  1301] loss: 0.49805544466811086
0.4475615620613098, [1,  1401] loss: 0.49611852645108223
0.4884079396724701, [1,  1501] loss: 0.49514238785537856
0.45078808069229126, [1,  1601] loss: 0.49394899189732805
0.3717554211616516, [1,  1701] loss: 0.493046568534712
0.4602692425251007, [1,  1801] loss: 0

0.6357227563858032, [1,   101] loss: 0.6805409777282488
0.49193131923675537, [1,   201] loss: 0.601772096471407
0.5439518690109253, [1,   301] loss: 0.5644952670185273
0.5365626215934753, [1,   401] loss: 0.544209124329976
0.45888397097587585, [1,   501] loss: 0.5331377634804644
0.548660933971405, [1,   601] loss: 0.5250652554179983
0.40660643577575684, [1,   701] loss: 0.5200638749587553
0.45078933238983154, [1,   801] loss: 0.5150585885388723
0.3757970929145813, [1,   901] loss: 0.5107253623028574
0.37275230884552, [1,  1001] loss: 0.5072998555003108
0.5229828953742981, [1,  1101] loss: 0.5055094519790794
0.5696892142295837, [1,  1201] loss: 0.5027580225993751
0.3887179493904114, [1,  1301] loss: 0.5006888018581704
0.5417091250419617, [1,  1401] loss: 0.49876482096593094
0.5067312717437744, [1,  1501] loss: 0.49745773909728896
0.5657249689102173, [1,  1601] loss: 0.49649694818842793
0.543014407157898, [1,  1701] loss: 0.49522208699683873
0.4580304026603699, [1,  1801] loss: 0.4942773

0.6100487112998962, [1,   101] loss: 0.6777949763996767
0.5485233068466187, [1,   201] loss: 0.6019380755388914
0.5069628357887268, [1,   301] loss: 0.5637323893977955
0.49087339639663696, [1,   401] loss: 0.5414200357888405
0.42709434032440186, [1,   501] loss: 0.5285741061923984
0.5677149295806885, [1,   601] loss: 0.5214015137583959
0.5530333518981934, [1,   701] loss: 0.5141204085822793
0.4990283250808716, [1,   801] loss: 0.5092281760385122
0.4803275465965271, [1,   901] loss: 0.5053958142802665
0.47826534509658813, [1,  1001] loss: 0.5030005157559544
0.5088731646537781, [1,  1101] loss: 0.5001183624407252
0.5200132727622986, [1,  1201] loss: 0.49819985609020817
0.49025362730026245, [1,  1301] loss: 0.49605646354935884
0.47614148259162903, [1,  1401] loss: 0.49437484450420255
0.49983325600624084, [1,  1501] loss: 0.4927337753085753
0.5115696787834167, [1,  1601] loss: 0.4915461047953326
0.4262208938598633, [1,  1701] loss: 0.49022522905971777
0.5270270109176636, [1,  1801] loss: 0

0.6358447670936584, [1,   101] loss: 0.6819736396912301
0.3830084502696991, [1,   201] loss: 0.6016262062449953
0.5076191425323486, [1,   301] loss: 0.5648581946014962
0.4404894709587097, [1,   401] loss: 0.545037155288116
0.5231925249099731, [1,   501] loss: 0.5340473541242634
0.5419783592224121, [1,   601] loss: 0.5250508851695577
0.48465466499328613, [1,   701] loss: 0.5186508681609185
0.5625101327896118, [1,   801] loss: 0.5132439436946766
0.5546771287918091, [1,   901] loss: 0.5096197241915186
0.4802311062812805, [1,  1001] loss: 0.5068864282164779
0.5231723189353943, [1,  1101] loss: 0.5035603188120377
0.5245060324668884, [1,  1201] loss: 0.501175723343368
0.4910752773284912, [1,  1301] loss: 0.49959485745952276
0.3822344243526459, [1,  1401] loss: 0.49735398214047166
0.4550856947898865, [1,  1501] loss: 0.49637342949734775
0.543838620185852, [1,  1601] loss: 0.49526858714168925
0.46667277812957764, [1,  1701] loss: 0.49410807079844166
0.4530283212661743, [1,  1801] loss: 0.49348

...

0.6430147886276245, [1,   101] loss: 0.6810222191385703
0.5596685409545898, [1,   201] loss: 0.6029179830159714
0.5373173356056213, [1,   301] loss: 0.5635105533358267
0.46244165301322937, [1,   401] loss: 0.5462358960709964
0.5041037797927856, [1,   501] loss: 0.5329971550526971
0.4622595012187958, [1,   601] loss: 0.5238261862275208
0.5249720811843872, [1,   701] loss: 0.5181881735438797
0.45772647857666016, [1,   801] loss: 0.5127749390035087
0.5184947848320007, [1,   901] loss: 0.5099530083258594
0.5192611217498779, [1,  1001] loss: 0.5080207923462579
0.3820582628250122, [1,  1101] loss: 0.5045494807107572
0.47371184825897217, [1,  1201] loss: 0.5021802230887766
0.48656603693962097, [1,  1301] loss: 0.499511683885177
0.546728253364563, [1,  1401] loss: 0.49757973969961217
0.5347222685813904, [1,  1501] loss: 0.49595966083379206
0.5425353050231934, [1,  1601] loss: 0.4948159120814045
0.5129165649414062, [1,  1701] loss: 0.49374178188608225
0.28827744722366333, [1,  1801] loss: 0.493

0.6521808505058289, [1,   101] loss: 0.6804224742521153
0.5046307444572449, [1,   201] loss: 0.6144219024560937
0.4252280294895172, [1,   301] loss: 0.5713809108813339
0.5465679168701172, [1,   401] loss: 0.5492704282154763
0.4401184022426605, [1,   501] loss: 0.5346291806110127
0.49520525336265564, [1,   601] loss: 0.525038567512682
0.4405885338783264, [1,   701] loss: 0.5195711076302127
0.5397289991378784, [1,   801] loss: 0.5140822778517536
0.4448229670524597, [1,   901] loss: 0.509256229499204
0.5150169134140015, [1,  1001] loss: 0.506439323831986
0.4491482079029083, [1,  1101] loss: 0.5033144912700237
0.5179452300071716, [1,  1201] loss: 0.5010606626686109
0.5335595607757568, [1,  1301] loss: 0.49864664749399135
0.5076864361763, [1,  1401] loss: 0.49700492956568565
0.4614611864089966, [1,  1501] loss: 0.49609517235107853
0.504402756690979, [1,  1601] loss: 0.4943883246663658
0.5778954029083252, [1,  1701] loss: 0.49304080191673355
0.48691660165786743, [1,  1801] loss: 0.4923021136

0.6274212598800659, [1,   101] loss: 0.6795009882143228
0.5126788020133972, [1,   201] loss: 0.5983007227010395
0.5850688815116882, [1,   301] loss: 0.5594512054888513
0.4838449954986572, [1,   401] loss: 0.5387803324291534
0.5567697882652283, [1,   501] loss: 0.5253961473822356
0.46211129426956177, [1,   601] loss: 0.5173972113408185
0.45797210931777954, [1,   701] loss: 0.5116147683154839
0.3993888199329376, [1,   801] loss: 0.5066173678071013
0.4619125425815582, [1,   901] loss: 0.5027757587198677
0.4304504990577698, [1,  1001] loss: 0.5007001440395247
0.4971389174461365, [1,  1101] loss: 0.49797981934153307
0.42201119661331177, [1,  1201] loss: 0.49598309283550335
0.4753815829753876, [1,  1301] loss: 0.4942204844805023
0.5479663610458374, [1,  1401] loss: 0.4925056909298063
0.4964839220046997, [1,  1501] loss: 0.4909655304053559
0.3927049934864044, [1,  1601] loss: 0.48974493976163536
0.3714561462402344, [1,  1701] loss: 0.4891584972155087
0.4954726994037628, [1,  1801] loss: 0.487

0.5882490277290344, [1,   101] loss: 0.6786983874764773
0.43627166748046875, [1,   201] loss: 0.602892123792895
0.575764000415802, [1,   301] loss: 0.5654480767210457
0.4292149245738983, [1,   401] loss: 0.5443766661861591
0.3575950264930725, [1,   501] loss: 0.5313420194589688
0.5187890529632568, [1,   601] loss: 0.5229014880248591
0.5688630938529968, [1,   701] loss: 0.5179317327436809
0.528864860534668, [1,   801] loss: 0.5138588373952739
0.38652077317237854, [1,   901] loss: 0.5106031575160603
0.46109020709991455, [1,  1001] loss: 0.506947516010596
0.5252242684364319, [1,  1101] loss: 0.503547973748124
0.5134909152984619, [1,  1201] loss: 0.5007035466256884
0.5574110150337219, [1,  1301] loss: 0.4992863578030369
0.40456271171569824, [1,  1401] loss: 0.4980524862816638
0.4480995535850525, [1,  1501] loss: 0.49656435420400374
0.5247041583061218, [1,  1601] loss: 0.49533925013271146
0.38467106223106384, [1,  1701] loss: 0.4939040507834354
0.4745214879512787, [1,  1801] loss: 0.4935408

0.6529759764671326, [1,   101] loss: 0.6803629203598098
0.4054172933101654, [1,   201] loss: 0.611870325323361
0.44299939274787903, [1,   301] loss: 0.5712730834056373
0.49021589756011963, [1,   401] loss: 0.5493148214501931
0.4834919571876526, [1,   501] loss: 0.5356973985474028
0.5347434282302856, [1,   601] loss: 0.5267021582894238
0.5736207962036133, [1,   701] loss: 0.5209078091740098
0.5261121988296509, [1,   801] loss: 0.515815741616242
0.5413112044334412, [1,   901] loss: 0.5120346930692516
0.5360214114189148, [1,  1001] loss: 0.5094378364759011
0.4573625922203064, [1,  1101] loss: 0.5061414229745328
0.4587925374507904, [1,  1201] loss: 0.5041387302616455
0.45868760347366333, [1,  1301] loss: 0.5012705777925679
0.513699471950531, [1,  1401] loss: 0.4996029725358114
0.479641318321228, [1,  1501] loss: 0.49726956186296145
0.4232467710971832, [1,  1601] loss: 0.495818751266716
0.5531078577041626, [1,  1701] loss: 0.49523417369573697
0.5478377938270569, [1,  1801] loss: 0.494282490

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_CNN_Uniform'
  loo_cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

  # Train model and log on wandb
  loo_cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

  # Save model to Drive
  torch.save(loo_cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_cnn_model.predict(test_dl, separate_words=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5109763145446777, [1,   101] loss: 0.650560727213869
0.3744698464870453, [1,   201] loss: 0.56471883183095
0.5105562806129456, [1,   301] loss: 0.5311721934630625
0.3284772038459778, [1,   401] loss: 0.5113033772704013
0.5071017742156982, [1,   501] loss: 0.5026381725441672
0.49548742175102234, [1,   601] loss: 0.49402496377362587
0.3865894675254822, [1,   701] loss: 0.487878779626947
0.403886079788208, [1,   801] loss: 0.48195210843348174
0.4959622323513031, [1,   901] loss: 0.4762354481398861
0.45943450927734375, [1,  1001] loss: 0.47019595896209276
0.3238782286643982, [1,  1101] loss: 0.4655431894742825
0.4572938084602356, [1,  1201] loss: 0.46236824634470214
0.4362674951553345, [1,  1301] loss: 0.45950542643471554
0.5087378025054932, [1,  1401] loss: 0.4562384181580826
0.4490806460380554, [1,  1501] loss: 0.4543710558971193
0.5056360960006714, [1,  1601] loss: 0.4517537635669047
0.41757169365882874, [1,  1701] loss: 0.44991665503896033
0.322038471698761, [1,  1801] loss: 0.448586

0.5673913955688477, [1,   101] loss: 0.6461810198160681
0.4038721024990082, [1,   201] loss: 0.559415706206317
0.5433730483055115, [1,   301] loss: 0.5237100264954805
0.41512438654899597, [1,   401] loss: 0.5088144183679114
0.4964577853679657, [1,   501] loss: 0.5005090572757873
0.39986100792884827, [1,   601] loss: 0.49166235250859414
0.49500253796577454, [1,   701] loss: 0.4829566069957023
0.5001325011253357, [1,   801] loss: 0.47782467115907634
0.43717148900032043, [1,   901] loss: 0.47370908769068787
0.5189933776855469, [1,  1001] loss: 0.4686241707691065
0.4520004689693451, [1,  1101] loss: 0.4648041333614102
0.41516607999801636, [1,  1201] loss: 0.46172828843303765
0.4874456226825714, [1,  1301] loss: 0.45945912099040354
0.3733276128768921, [1,  1401] loss: 0.45637336910451676
0.41643255949020386, [1,  1501] loss: 0.45445281204622956
0.3751693069934845, [1,  1601] loss: 0.4524498881957145
0.290732204914093, [1,  1701] loss: 0.45084058927445464
0.42234188318252563, [1,  1801] loss

0.5474735498428345, [1,   101] loss: 0.6495474447118174
0.4720084071159363, [1,   201] loss: 0.5635667425483021
0.5341393351554871, [1,   301] loss: 0.5316237810244195
0.542880654335022, [1,   401] loss: 0.5127270295287011
0.356160044670105, [1,   501] loss: 0.5031058742495592
0.5478101968765259, [1,   601] loss: 0.4963665878316527
0.34669846296310425, [1,   701] loss: 0.4918280545935651
0.40759238600730896, [1,   801] loss: 0.4868598746486966
0.24166536331176758, [1,   901] loss: 0.4821185140181064
0.26693594455718994, [1,  1001] loss: 0.4791846774912976
0.5110103487968445, [1,  1101] loss: 0.4777799878035969
0.5469383001327515, [1,  1201] loss: 0.47437335349786885
0.21996553242206573, [1,  1301] loss: 0.47116537035931816
0.5154864192008972, [1,  1401] loss: 0.46799422506984856
0.4940853714942932, [1,  1501] loss: 0.4657051660949433
0.5192405581474304, [1,  1601] loss: 0.4639013344648851
0.5167546272277832, [1,  1701] loss: 0.46151749540924114
0.4191707372665405, [1,  1801] loss: 0.45

0.550811231136322, [1,   101] loss: 0.6586934121528475
0.5495235919952393, [1,   201] loss: 0.5725541137047668
0.5228588581085205, [1,   301] loss: 0.5360407612450495
0.49033308029174805, [1,   401] loss: 0.5152392887563777
0.41005823016166687, [1,   501] loss: 0.5031160751502671
0.5564361810684204, [1,   601] loss: 0.4970015626580465
0.5600501894950867, [1,   701] loss: 0.4899069299541424
0.5002467036247253, [1,   801] loss: 0.48567612941717536
0.4574111998081207, [1,   901] loss: 0.4816140859459137
0.4313989281654358, [1,  1001] loss: 0.47920901661033516
0.48558616638183594, [1,  1101] loss: 0.47572369707052975
0.4812975823879242, [1,  1201] loss: 0.47239741290935766
0.45776045322418213, [1,  1301] loss: 0.4686280787678337
0.4294682741165161, [1,  1401] loss: 0.46537138022838703
0.46472740173339844, [1,  1501] loss: 0.46235020474582256
0.4699678421020508, [1,  1601] loss: 0.45992586000832375
0.35880884528160095, [1,  1701] loss: 0.4574946124086935
0.4799494743347168, [1,  1801] loss:

0.554996907711029, [1,   101] loss: 0.6514432377154284
0.4700274169445038, [1,   201] loss: 0.5616626785465734
0.47750839591026306, [1,   301] loss: 0.5278757944257553
0.3959384858608246, [1,   401] loss: 0.5123417915548767
0.48406338691711426, [1,   501] loss: 0.5015184201761158
0.5323628783226013, [1,   601] loss: 0.4931707172197431
0.44157522916793823, [1,   701] loss: 0.48714822481855347
0.5452555418014526, [1,   801] loss: 0.4809816965598441
0.5631605982780457, [1,   901] loss: 0.4778724167243754
0.4298436641693115, [1,  1001] loss: 0.47510326819700915
0.527135968208313, [1,  1101] loss: 0.4715707080403206
0.5279970765113831, [1,  1201] loss: 0.4689742900946059
0.46910107135772705, [1,  1301] loss: 0.4678388128227495
0.33998313546180725, [1,  1401] loss: 0.4655282123228382
0.4279932677745819, [1,  1501] loss: 0.4642300043083841
0.5126274824142456, [1,  1601] loss: 0.46273653245508334
0.4187160134315491, [1,  1701] loss: 0.46100686030623356
0.37262555956840515, [1,  1801] loss: 0.4

...

0.5860051512718201, [1,   101] loss: 0.6512360333806217
0.5647640824317932, [1,   201] loss: 0.5630842003952804
0.5513307452201843, [1,   301] loss: 0.5281749990493356
0.4453325867652893, [1,   401] loss: 0.5145932653746997
0.4957638382911682, [1,   501] loss: 0.5018226015651059
0.4178754687309265, [1,   601] loss: 0.49322789029749775
0.5270048379898071, [1,   701] loss: 0.4885582820580111
0.4293270707130432, [1,   801] loss: 0.48335270509216816
0.5065409541130066, [1,   901] loss: 0.48099118146991626
0.5136945247650146, [1,  1001] loss: 0.47994576142979906
0.3712556064128876, [1,  1101] loss: 0.47611953947459645
0.435286283493042, [1,  1201] loss: 0.4742848974009735
0.4432455897331238, [1,  1301] loss: 0.471424631940503
0.5312374234199524, [1,  1401] loss: 0.46914427256813906
0.5109866857528687, [1,  1501] loss: 0.46678980165406275
0.4964241683483124, [1,  1601] loss: 0.4647802425261068
0.46507078409194946, [1,  1701] loss: 0.46309212044643555
0.1844327598810196, [1,  1801] loss: 0.46

0.5414738059043884, [1,   101] loss: 0.6429567018357834
0.48944759368896484, [1,   201] loss: 0.5655742765066043
0.3643814027309418, [1,   301] loss: 0.5301408624134191
0.5250642895698547, [1,   401] loss: 0.510831118075925
0.40634259581565857, [1,   501] loss: 0.4965150397337839
0.4695602059364319, [1,   601] loss: 0.4888811883285716
0.40939998626708984, [1,   701] loss: 0.4847451854449366
0.5380936861038208, [1,   801] loss: 0.4808154385002067
0.40198278427124023, [1,   901] loss: 0.4766932251913831
0.5124511122703552, [1,  1001] loss: 0.4742690515178781
0.4232638478279114, [1,  1101] loss: 0.47127568133033265
0.5183993577957153, [1,  1201] loss: 0.4689374715462017
0.5310912728309631, [1,  1301] loss: 0.4662741865908339
0.4803682863712311, [1,  1401] loss: 0.46426847632402696
0.42149078845977783, [1,  1501] loss: 0.4627956222646003
0.43813878297805786, [1,  1601] loss: 0.46014326974647185
0.5544416904449463, [1,  1701] loss: 0.45808134076877033
0.4409034848213196, [1,  1801] loss: 0.

0.5724218487739563, [1,   101] loss: 0.6566154868295877
0.47683173418045044, [1,   201] loss: 0.57370997201744
0.5628429651260376, [1,   301] loss: 0.5351453963110218
0.4736681580543518, [1,   401] loss: 0.513498979465028
0.5504884719848633, [1,   501] loss: 0.49934593214841183
0.42568010091781616, [1,   601] loss: 0.49084878924880765
0.4542081356048584, [1,   701] loss: 0.4848966584055978
0.33408740162849426, [1,   801] loss: 0.47893898216972636
0.4578634202480316, [1,   901] loss: 0.4745380773263819
0.37876448035240173, [1,  1001] loss: 0.47240428613139673
0.44206979870796204, [1,  1101] loss: 0.4690686381074323
0.35956379771232605, [1,  1201] loss: 0.465846106050215
0.4344451427459717, [1,  1301] loss: 0.4627421209896463
0.5216638445854187, [1,  1401] loss: 0.4599257028375159
0.46129110455513, [1,  1501] loss: 0.4572754107083105
0.30701547861099243, [1,  1601] loss: 0.45503375630390636
0.30642905831336975, [1,  1701] loss: 0.4536541296954298
0.45904573798179626, [1,  1801] loss: 0.4

0.5330172777175903, [1,   101] loss: 0.6550170973976059
0.37729427218437195, [1,   201] loss: 0.5705701673208777
0.5568580031394958, [1,   301] loss: 0.5365462599204625
0.34391656517982483, [1,   401] loss: 0.5138755316969165
0.27080732583999634, [1,   501] loss: 0.5008094727160212
0.49326062202453613, [1,   601] loss: 0.4936672181833207
0.5482082366943359, [1,   701] loss: 0.4892890340889061
0.5558379292488098, [1,   801] loss: 0.48562584423021726
0.3234045207500458, [1,   901] loss: 0.48224328359078356
0.40200909972190857, [1,  1001] loss: 0.4783647042530757
0.5082688331604004, [1,  1101] loss: 0.47408369115869314
0.4854549467563629, [1,  1201] loss: 0.4699408250684841
0.5112707018852234, [1,  1301] loss: 0.4674982536901977
0.3361773192882538, [1,  1401] loss: 0.46530302272023344
0.426691472530365, [1,  1501] loss: 0.46287643793302724
0.4712468385696411, [1,  1601] loss: 0.46072252154313054
0.3321051299571991, [1,  1701] loss: 0.45821150171097974
0.4144241213798523, [1,  1801] loss: 

0.5851743221282959, [1,   101] loss: 0.6481112359773995
0.35898351669311523, [1,   201] loss: 0.5681176792033276
0.43245258927345276, [1,   301] loss: 0.5329377860622945
0.4793151319026947, [1,   401] loss: 0.5130456437791078
0.4664614498615265, [1,   501] loss: 0.5014025539516689
0.5430395007133484, [1,   601] loss: 0.4945228652232102
0.5474388003349304, [1,   701] loss: 0.4905192136084302
0.5209752917289734, [1,   801] loss: 0.4860706091782871
0.5442140698432922, [1,   901] loss: 0.48408346298201366
0.5259814858436584, [1,  1001] loss: 0.48243972404555724
0.43207600712776184, [1,  1101] loss: 0.47920726606458236
0.418913334608078, [1,  1201] loss: 0.47669958366045445
0.4140640199184418, [1,  1301] loss: 0.4730932666396838
0.491232693195343, [1,  1401] loss: 0.471000279351101
0.43403077125549316, [1,  1501] loss: 0.46763438769652793
0.36986279487609863, [1,  1601] loss: 0.46528201851339956
0.514196515083313, [1,  1701] loss: 0.4639870900483358
0.5128870010375977, [1,  1801] loss: 0.46

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/LOO'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/LOO'

for lang in languages:
  # Set random seeds
  random.seed(seed)
  np.random.seed(seed)
  torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
  torch.manual_seed(seed)

  # Set Datasets
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
    loo_train_ds = pickle.load(f)
  with open(os.path.join(data_folder, 'Uniform', 'LOO', f'LOO_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
    loo_val_ds = pickle.load(f)

  # Set samplers and DataLoaders
  train_sampler = EqualLengthsBatchSampler(loo_train_ds, batch_size, seed)
  train_dl = DataLoader(loo_train_ds, batch_sampler=train_sampler)
  val_sampler = EqualLengthsBatchSampler(loo_val_ds, batch_size, seed)
  val_dl = DataLoader(loo_val_ds, batch_sampler=val_sampler)

  # Set up model
  model_name = f'LOO_{lang[1]}_LSTM_Uniform'
  loo_lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

  # Train model and log on wandb
  loo_lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

  # Save model to Drive
  torch.save(loo_lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

  # Run predictions on Test Dataloader
  test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
  preds, sylls = loo_lstm_model.predict(test_dl, separate_words=True, lstm=True)

  # Format predictions, ground truths, languages, word indices, positions, and segments
  # to feed into Pandas DataFrame
  new_preds = [entry for row in preds for entry in row.cpu().numpy()]
  new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
  sylls_check = [entry for row in test_ds for entry in row[1]]
  new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
  new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
  new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
  new_segments = [segment for entry in test_ds for segment in entry[3]]
  for i in range(len(sylls_check)):
    assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

  loo_lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                            'Positions':new_positions, 'Segments':new_segments})

  loo_lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5117418766021729, [1,   101] loss: 0.6349995859188609
0.26722654700279236, [1,   201] loss: 0.5784264508616271
0.5177597403526306, [1,   301] loss: 0.5459240846756684
0.3323812484741211, [1,   401] loss: 0.5236130338580234
0.5235074162483215, [1,   501] loss: 0.5134676470906435
0.5179975628852844, [1,   601] loss: 0.5039246431652599
0.4022185206413269, [1,   701] loss: 0.49675271510227603
0.4159891605377197, [1,   801] loss: 0.49108872345919613
0.47997575998306274, [1,   901] loss: 0.48656392304204016
0.48761484026908875, [1,  1001] loss: 0.4818317897461511
0.342171311378479, [1,  1101] loss: 0.4784826570673491
0.49895793199539185, [1,  1201] loss: 0.4768054845752962
0.4748489558696747, [1,  1301] loss: 0.47514574937551046
0.55573570728302, [1,  1401] loss: 0.4726640847348724
0.44933876395225525, [1,  1501] loss: 0.47184832524173187
0.5397490859031677, [1,  1601] loss: 0.47007269091638904
0.453876256942749, [1,  1701] loss: 0.4691405245165906
0.32596731185913086, [1,  1801] loss: 0.4

0.6046152114868164, [1,   101] loss: 0.6373623479710947
0.43936726450920105, [1,   201] loss: 0.583011120557785
0.547476589679718, [1,   301] loss: 0.542881750981277
0.427094429731369, [1,   401] loss: 0.5242594641788939
0.49881479144096375, [1,   501] loss: 0.5137303874878112
0.4099898338317871, [1,   601] loss: 0.5036153603413339
0.5074957013130188, [1,   701] loss: 0.4939914811907413
0.5007166266441345, [1,   801] loss: 0.4889482461967123
0.44961681962013245, [1,   901] loss: 0.4851277746284974
0.5516555309295654, [1,  1001] loss: 0.4809760088984902
0.48023414611816406, [1,  1101] loss: 0.4780507009750491
0.46535181999206543, [1,  1201] loss: 0.47588877228525256
0.4904136657714844, [1,  1301] loss: 0.47466536241939306
0.43529731035232544, [1,  1401] loss: 0.4725853894264846
0.4197425842285156, [1,  1501] loss: 0.4714283195338513
0.4363362789154053, [1,  1601] loss: 0.47019338987530357
0.28981995582580566, [1,  1701] loss: 0.4690687925166624
0.4456017315387726, [1,  1801] loss: 0.468

0.5979421138763428, [1,   101] loss: 0.6431105384732237
0.5042997598648071, [1,   201] loss: 0.5913857974816318
0.5363005995750427, [1,   301] loss: 0.5536276672864673
0.5484806895256042, [1,   401] loss: 0.5307522811125639
0.36366114020347595, [1,   501] loss: 0.5182372930342566
0.5479428768157959, [1,   601] loss: 0.5097333242165268
0.35782697796821594, [1,   701] loss: 0.5039961510012392
0.4238813817501068, [1,   801] loss: 0.49806895314456523
0.25661614537239075, [1,   901] loss: 0.4925430908088017
0.26512816548347473, [1,  1001] loss: 0.48872292620854657
0.5194698572158813, [1,  1101] loss: 0.4872325111610255
0.5558388829231262, [1,  1201] loss: 0.48425580863899037
0.21633240580558777, [1,  1301] loss: 0.4817912638599739
0.5658538341522217, [1,  1401] loss: 0.4796640327004855
0.5056043863296509, [1,  1501] loss: 0.47839361542387854
0.5512093901634216, [1,  1601] loss: 0.4776366443316837
0.5742123126983643, [1,  1701] loss: 0.47638023805436075
0.43227389454841614, [1,  1801] loss: 

0.5430070757865906, [1,   101] loss: 0.6394169106341825
0.5686913728713989, [1,   201] loss: 0.5869105339643375
0.5192807912826538, [1,   301] loss: 0.5491114562235005
0.5025238990783691, [1,   401] loss: 0.525360345171574
0.4198184013366699, [1,   501] loss: 0.5121612275194027
0.5546257495880127, [1,   601] loss: 0.505103601344215
0.5568979978561401, [1,   701] loss: 0.49701224433287405
0.5044249296188354, [1,   801] loss: 0.49209843796402325
0.4546927809715271, [1,   901] loss: 0.4876336609400999
0.4404571056365967, [1,  1001] loss: 0.48510223784140655
0.5291025042533875, [1,  1101] loss: 0.48205100881658175
0.521992027759552, [1,  1201] loss: 0.48013580833669506
0.4741746485233307, [1,  1301] loss: 0.47778149023022126
0.4521574079990387, [1,  1401] loss: 0.4758166668406135
0.48858514428138733, [1,  1501] loss: 0.47396889925102326
0.5040178298950195, [1,  1601] loss: 0.4726579828766046
0.36915943026542664, [1,  1701] loss: 0.47131596768887024
0.5225086212158203, [1,  1801] loss: 0.46

0.5942984819412231, [1,   101] loss: 0.6415399324775922
0.2528327405452728, [1,   201] loss: 0.5819620709514144
0.486044704914093, [1,   301] loss: 0.5454370061622505
0.3999800682067871, [1,   401] loss: 0.5245197842691902
0.4872515797615051, [1,   501] loss: 0.5120444686231975
0.5366538763046265, [1,   601] loss: 0.5023512136618825
0.45077359676361084, [1,   701] loss: 0.49513231213609776
0.5440153479576111, [1,   801] loss: 0.4882487507720714
0.5674633979797363, [1,   901] loss: 0.4845388947089888
0.4280644953250885, [1,  1001] loss: 0.4814241794044976
0.5239330530166626, [1,  1101] loss: 0.47747181731865795
0.5353283286094666, [1,  1201] loss: 0.4745889417765093
0.47235751152038574, [1,  1301] loss: 0.4733173623881507
0.34833279252052307, [1,  1401] loss: 0.4710945078091354
0.45625320076942444, [1,  1501] loss: 0.4701521429124671
0.5190907716751099, [1,  1601] loss: 0.46932564237661695
0.4470404386520386, [1,  1701] loss: 0.46836605645510326
0.44326379895210266, [1,  1801] loss: 0.4

...

0.593403697013855, [1,   101] loss: 0.6423017943259512
0.5794522762298584, [1,   201] loss: 0.5878523586697839
0.55430006980896, [1,   301] loss: 0.5485760522047151
0.4457559585571289, [1,   401] loss: 0.5312118798568659
0.4977310001850128, [1,   501] loss: 0.5153519669157303
0.4333319067955017, [1,   601] loss: 0.5050984041861408
0.5313850045204163, [1,   701] loss: 0.49930975859328447
0.4305869936943054, [1,   801] loss: 0.49315990326221515
0.5071058869361877, [1,   901] loss: 0.4900999523442937
0.5168107748031616, [1,  1001] loss: 0.4884922046299938
0.37152543663978577, [1,  1101] loss: 0.48429155737486457
0.4405606687068939, [1,  1201] loss: 0.48207612130031
0.43456047773361206, [1,  1301] loss: 0.479226645637736
0.5321016311645508, [1,  1401] loss: 0.47728010301852464
0.5390729308128357, [1,  1501] loss: 0.47532690965448277
0.5183489322662354, [1,  1601] loss: 0.47390964378060063
0.4790876805782318, [1,  1701] loss: 0.47277098142710033
0.19102780520915985, [1,  1801] loss: 0.47232

0.611302375793457, [1,   101] loss: 0.6384722248162373
0.5302747488021851, [1,   201] loss: 0.5932665461331458
0.37670832872390747, [1,   301] loss: 0.5512404445298883
0.5301542282104492, [1,   401] loss: 0.5268211691382519
0.39191943407058716, [1,   501] loss: 0.5107000394912061
0.4759744703769684, [1,   601] loss: 0.5013615166932691
0.41606491804122925, [1,   701] loss: 0.4961751748126176
0.5404819846153259, [1,   801] loss: 0.49091121267420373
0.4044014811515808, [1,   901] loss: 0.4860994705473477
0.5212534666061401, [1,  1001] loss: 0.4831273223010155
0.43611815571784973, [1,  1101] loss: 0.47978316173363444
0.5320170521736145, [1,  1201] loss: 0.47742057727846776
0.5548105835914612, [1,  1301] loss: 0.4752221912128434
0.5065544843673706, [1,  1401] loss: 0.4736897464360321
0.45618024468421936, [1,  1501] loss: 0.4729634151234975
0.47053658962249756, [1,  1601] loss: 0.4708577179879899
0.5637781023979187, [1,  1701] loss: 0.46952462615308377
0.48439112305641174, [1,  1801] loss: 0

0.5846754312515259, [1,   101] loss: 0.6398084010228072
0.5023480653762817, [1,   201] loss: 0.5815740788160865
0.5663903951644897, [1,   301] loss: 0.5438746861940207
0.4799453616142273, [1,   401] loss: 0.5212559044509755
0.5473951101303101, [1,   501] loss: 0.5060182221516402
0.43021172285079956, [1,   601] loss: 0.49696079285787464
0.45865142345428467, [1,   701] loss: 0.49047346058143526
0.34159544110298157, [1,   801] loss: 0.48424082897724435
0.46138912439346313, [1,   901] loss: 0.4798032289472193
0.38730761408805847, [1,  1001] loss: 0.47785769730478855
0.4600098133087158, [1,  1101] loss: 0.47510525842724227
0.35539066791534424, [1,  1201] loss: 0.47263275220878515
0.47032225131988525, [1,  1301] loss: 0.47071256739968614
0.5529501438140869, [1,  1401] loss: 0.4690296304259957
0.4970400035381317, [1,  1501] loss: 0.4675231529505232
0.3136201798915863, [1,  1601] loss: 0.46642342745922716
0.32192811369895935, [1,  1701] loss: 0.4663413549384112
0.48956626653671265, [1,  1801] 

0.5291242599487305, [1,   101] loss: 0.6335543214094521
0.4286568760871887, [1,   201] loss: 0.5822265532182817
0.5587719082832336, [1,   301] loss: 0.5476666446342024
0.35292837023735046, [1,   401] loss: 0.5233755246956747
0.27921023964881897, [1,   501] loss: 0.5095907638589303
0.486939936876297, [1,   601] loss: 0.5007890714162003
0.5471712350845337, [1,   701] loss: 0.4958163712933638
0.560607373714447, [1,   801] loss: 0.4916932077313333
0.32091689109802246, [1,   901] loss: 0.48793058488497326
0.40382251143455505, [1,  1001] loss: 0.48365083006354836
0.53449547290802, [1,  1101] loss: 0.4795962597000718
0.5050679445266724, [1,  1201] loss: 0.47628208130697325
0.5502620935440063, [1,  1301] loss: 0.47491389618961743
0.3442721962928772, [1,  1401] loss: 0.47368932484538107
0.468565970659256, [1,  1501] loss: 0.47237245936559724
0.5254090428352356, [1,  1601] loss: 0.47113375841808053
0.33825886249542236, [1,  1701] loss: 0.46948499718723685
0.42519611120224, [1,  1801] loss: 0.469

0.6045477986335754, [1,   101] loss: 0.6406463349219595
0.4173644483089447, [1,   201] loss: 0.5870963788744229
0.4396524429321289, [1,   301] loss: 0.549822386713123
0.48587566614151, [1,   401] loss: 0.526902300684232
0.47765985131263733, [1,   501] loss: 0.5134404277551674
0.5364841222763062, [1,   601] loss: 0.5048086903555421
0.5449034571647644, [1,   701] loss: 0.49976937100822677
0.5224985480308533, [1,   801] loss: 0.49443717905495793
0.5428994297981262, [1,   901] loss: 0.49155523175669297
0.5265424251556396, [1,  1001] loss: 0.4894462947721605
0.4675789773464203, [1,  1101] loss: 0.48629816829292044
0.4343566298484802, [1,  1201] loss: 0.4841930724922366
0.43006256222724915, [1,  1301] loss: 0.4812348234616821
0.5064359307289124, [1,  1401] loss: 0.47981413119312355
0.4284214973449707, [1,  1501] loss: 0.47692671407269766
0.3811142146587372, [1,  1601] loss: 0.47539217127888445
0.5547375082969666, [1,  1701] loss: 0.4750286604922214
0.5118553638458252, [1,  1801] loss: 0.4733

## Language Families

In [ ]:
# Test Dataset is shared between All Languages, LOO, and Family
with open(os.path.join(data_folder, 'Uniform', 'All_Langs_Test_Uniform.pickle'), 'rb') as f:
  test_ds = pickle.load(f)

In [ ]:
#@title Train FNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_FNN_Uniform'
    family_fnn_model = NgramFNN(n_gram=7, d_hidden=15, n_layers=5).to(device)

    # Train model and log on wandb
    family_fnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

    # Save model to Drive
    torch.save(family_fnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_fnn_model.predict(test_dl, separate_words=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_fnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_fnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.6298107504844666, [1,   101] loss: 0.6766092700533347
0.44269096851348877, [1,   201] loss: 0.5944129375379477
0.46868443489074707, [1,   301] loss: 0.5455311612037329
0.39022189378738403, [1,   401] loss: 0.5194148069753909

Validation Loss
tensor(0.4554)

0.433965802192688, [1,   101] loss: 0.43294498619466726
0.4778042733669281, [1,   201] loss: 0.4324371711679952
0.43174415826797485, [1,   301] loss: 0.43561487295896906
0.4313175678253174, [1,   401] loss: 0.4330092093668079

Validation Loss
tensor(0.4457)

0.4022732675075531, [1,   101] loss: 0.43131538989520307
0.40392041206359863, [1,   201] loss: 0.4251759780283591
0.35872310400009155, [1,   301] loss: 0.4295896844214379
0.43934953212738037, [1,   401] loss: 0.42736657580681275

Validation Loss
tensor(0.4432)

0.46020886301994324, [1,   101] loss: 0.42871085104375783
0.4727802872657776, [1,   201] loss: 0.428551032101337
0.3021039068698883, [1,   301] loss: 0.4231109296364642
0.42960116267204285, [1,   401] loss: 0.4237804021

0.6227216720581055, [1,   101] loss: 0.6752090330171113
0.4349915087223053, [1,   201] loss: 0.5981885700380031
0.4882972538471222, [1,   301] loss: 0.5508819458096527
0.43656209111213684, [1,   401] loss: 0.5219362646415644

Validation Loss
tensor(0.4427)

0.3430013656616211, [1,   101] loss: 0.4343762374160313
0.4931853711605072, [1,   201] loss: 0.437062845153002
0.3985360860824585, [1,   301] loss: 0.4362804240166547
0.4309267997741699, [1,   401] loss: 0.4346526101640335

Validation Loss
tensor(0.4373)

0.49416908621788025, [1,   101] loss: 0.4308726265288816
0.414144366979599, [1,   201] loss: 0.4317622552463664
0.43645110726356506, [1,   301] loss: 0.4297027175014597
0.41674867272377014, [1,   401] loss: 0.4294300491078536

Validation Loss
tensor(0.4369)

0.5920080542564392, [1,   101] loss: 0.4276799111083002
0.43186256289482117, [1,   201] loss: 0.4266668620394237
0.5556604862213135, [1,   301] loss: 0.42690976275954134
0.4250742495059967, [1,   401] loss: 0.42507041693476966


0.6141003370285034, [1,   101] loss: 0.6769266205258889
0.4774312376976013, [1,   201] loss: 0.6019923738875792
0.564918041229248, [1,   301] loss: 0.554203900684946
0.4158671498298645, [1,   401] loss: 0.5281989364849956

Validation Loss
tensor(0.4349)

0.41403746604919434, [1,   101] loss: 0.43198147585781493
0.33744198083877563, [1,   201] loss: 0.43338481744575263
0.5300326347351074, [1,   301] loss: 0.43937819163961667
0.5374963879585266, [1,   401] loss: 0.43959377860264887

Validation Loss
tensor(0.4279)

0.40159687399864197, [1,   101] loss: 0.4382688279199128
0.478877991437912, [1,   201] loss: 0.43503369613369897
0.41465339064598083, [1,   301] loss: 0.43452230313687623
0.49597740173339844, [1,   401] loss: 0.43537622184824765

Validation Loss
tensor(0.4296)

0.4829324781894684, [1,   101] loss: 0.4333115349901785
0.43052417039871216, [1,   201] loss: 0.42879998713583495
0.5236721038818359, [1,   301] loss: 0.4272352173379885
0.44503211975097656, [1,   401] loss: 0.4297737674

0.5815446972846985, [1,   101] loss: 0.6810247125011859
0.5444502830505371, [1,   201] loss: 0.6114716412712685
0.5783503651618958, [1,   301] loss: 0.5831742565893255
0.5958085060119629, [1,   401] loss: 0.566916560740245

Validation Loss
tensor(0.5109)

0.4726357161998749, [1,   101] loss: 0.5140718181829641
0.5243892669677734, [1,   201] loss: 0.5146503487777947
0.447674959897995, [1,   301] loss: 0.5093588099824233
0.5560040473937988, [1,   401] loss: 0.509966217334431

Validation Loss
tensor(0.5048)

0.5957070589065552, [1,   101] loss: 0.5092065838894041
0.48680657148361206, [1,   201] loss: 0.5083638015967696
0.5242598652839661, [1,   301] loss: 0.5079718623248446
0.4697684645652771, [1,   401] loss: 0.5060323297680167

Validation Loss
tensor(0.5092)

0.4217354953289032, [1,   101] loss: 0.5054162106301525
0.33375707268714905, [1,   201] loss: 0.5046654947065002
0.5120036602020264, [1,   301] loss: 0.5048329191548484
0.40569639205932617, [1,   401] loss: 0.5028266077698614

Vali

0.6309925317764282, [1,   101] loss: 0.6784668966095047
0.566356360912323, [1,   201] loss: 0.596886540304369
0.526656448841095, [1,   301] loss: 0.5682554697970615
0.4923340082168579, [1,   401] loss: 0.5493572380700313

Validation Loss
tensor(0.5403)

0.4109386205673218, [1,   101] loss: 0.4871651807633957
0.3322663903236389, [1,   201] loss: 0.48651102125941226
0.4645460546016693, [1,   301] loss: 0.49104553431371517
0.4400259554386139, [1,   401] loss: 0.48992934867628196

Validation Loss
tensor(0.5363)

0.4138188362121582, [1,   101] loss: 0.48050132629894976
0.4694647192955017, [1,   201] loss: 0.48362310727437335
0.5517762899398804, [1,   301] loss: 0.48734266060927384
0.32666096091270447, [1,   401] loss: 0.48514561451729993

Validation Loss
tensor(0.5394)

0.43189629912376404, [1,   101] loss: 0.48117753819073783
0.517438530921936, [1,   201] loss: 0.48329801457141763
0.5570330023765564, [1,   301] loss: 0.4804178881783818
0.2863140404224396, [1,   401] loss: 0.480340848131072

0.623417854309082, [1,   101] loss: 0.6804202122263389
0.6043083071708679, [1,   201] loss: 0.6110314872134385
0.5688959956169128, [1,   301] loss: 0.5777852480791732
0.3942086100578308, [1,   401] loss: 0.5628553706214315

Validation Loss
tensor(0.5175)

0.47122129797935486, [1,   101] loss: 0.5047839219027227
0.531095027923584, [1,   201] loss: 0.503413987174556
0.3740207552909851, [1,   301] loss: 0.5009581139218372
0.5867297649383545, [1,   401] loss: 0.5027948849441999

Validation Loss
tensor(0.5206)

0.5704731345176697, [1,   101] loss: 0.500255691828114
0.4956236481666565, [1,   201] loss: 0.4999501343390242
0.4399503469467163, [1,   301] loss: 0.49915609555783064
0.4632743299007416, [1,   401] loss: 0.4967928423251297

Validation Loss
tensor(0.5249)

0.5698314309120178, [1,   101] loss: 0.5061256555047365
0.5176700949668884, [1,   201] loss: 0.49719209605781595
0.5585790872573853, [1,   301] loss: 0.4923750003211918
0.42991364002227783, [1,   401] loss: 0.4930459684936186

Vali

0.6051095724105835, [1,   101] loss: 0.675895895108138
0.4975120425224304, [1,   201] loss: 0.5983115565124436

Validation Loss
tensor(0.4779)

0.47551798820495605, [1,   101] loss: 0.45017579610985103
0.39074376225471497, [1,   201] loss: 0.44929948122940255

Validation Loss
tensor(0.4660)

0.4101336896419525, [1,   101] loss: 0.44165388605382183
0.4115372598171234, [1,   201] loss: 0.43874282297210315

Validation Loss
tensor(0.4579)

0.4576660096645355, [1,   101] loss: 0.43446020383645995
0.4518223702907562, [1,   201] loss: 0.43432607609241164

Validation Loss
tensor(0.4519)

0.39037930965423584, [1,   101] loss: 0.42868661526406165
0.3474971652030945, [1,   201] loss: 0.4304693940267041

Validation Loss
tensor(0.4496)

0.4227997064590454, [1,   101] loss: 0.42257246227547673
0.37872588634490967, [1,   201] loss: 0.42823675497254327

Validation Loss
tensor(0.4470)

0.4942309260368347, [1,   101] loss: 0.4248072602371178
0.3939926028251648, [1,   201] loss: 0.4246202738427404

Valid

0.6343766450881958, [1,   101] loss: 0.6773268916819355
0.4406750202178955, [1,   201] loss: 0.6000423813933757

Validation Loss
tensor(0.4572)

0.5319442749023438, [1,   101] loss: 0.46742520946087224
0.4233945608139038, [1,   201] loss: 0.4607253575799477

Validation Loss
tensor(0.4436)

0.41500240564346313, [1,   101] loss: 0.4520766023952182
0.5071364045143127, [1,   201] loss: 0.4511448916659426

Validation Loss
tensor(0.4419)

0.3936847746372223, [1,   101] loss: 0.44730520012355085
0.4024001955986023, [1,   201] loss: 0.4499929404229074

Validation Loss
tensor(0.4386)

0.43818458914756775, [1,   101] loss: 0.44333173010018795
0.5226064324378967, [1,   201] loss: 0.4465361929206706

Validation Loss
tensor(0.4365)

0.5290032029151917, [1,   101] loss: 0.44886114795019133
0.5106412172317505, [1,   201] loss: 0.44481187339742384

Validation Loss
tensor(0.4403)

0.4767563045024872, [1,   101] loss: 0.43670616557102393
0.5331850647926331, [1,   201] loss: 0.4424851594576195

Validatio

In [ ]:
#@title Train CNN

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_CNN_Uniform'
    family_cnn_model = NgramCNN(n_gram=7, n_filters=15, n_layers=10).to(device)

    # Train model and log on wandb
    family_cnn_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name)

    # Save model to Drive
    torch.save(family_cnn_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_cnn_model.predict(test_dl, separate_words=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_cnn_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_cnn_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5594364404678345, [1,   101] loss: 0.6522430700830893
0.41819077730178833, [1,   201] loss: 0.5534298405125366
0.4456504285335541, [1,   301] loss: 0.5059785357741422
0.3198966979980469, [1,   401] loss: 0.4790337074947476

Validation Loss
tensor(0.4428)

0.41889411211013794, [1,   101] loss: 0.39349592587735394
0.4601604640483856, [1,   201] loss: 0.3893426208946835
0.4233861565589905, [1,   301] loss: 0.3928530480081457
0.37413057684898376, [1,   401] loss: 0.38830366491007984

Validation Loss
tensor(0.4268)

0.37256887555122375, [1,   101] loss: 0.3760268727667851
0.332375168800354, [1,   201] loss: 0.364993057570499
0.27416494488716125, [1,   301] loss: 0.3677628775346913
0.3929080367088318, [1,   401] loss: 0.3623528940942222

Validation Loss
tensor(0.4008)

0.3618438243865967, [1,   101] loss: 0.3508984178747281
0.40951070189476013, [1,   201] loss: 0.3523644565868734
0.2074071764945984, [1,   301] loss: 0.3448336325907628
0.39197084307670593, [1,   401] loss: 0.345991001443524

0.6109502911567688, [1,   101] loss: 0.6558549504468937
0.4174811542034149, [1,   201] loss: 0.5764887565700569
0.4807022511959076, [1,   301] loss: 0.532179976222523
0.41118448972702026, [1,   401] loss: 0.5042734196284168

Validation Loss
tensor(0.3955)

0.2956720292568207, [1,   101] loss: 0.4319963465527733
0.5154844522476196, [1,   201] loss: 0.43062700027257056
0.3900164067745209, [1,   301] loss: 0.4284129196722246
0.4433625340461731, [1,   401] loss: 0.42420504448419794

Validation Loss
tensor(0.3770)

0.43904250860214233, [1,   101] loss: 0.39294888263586725
0.34454575181007385, [1,   201] loss: 0.3831156571928541
0.36018291115760803, [1,   301] loss: 0.37598384867276863
0.3464244306087494, [1,   401] loss: 0.3721903761165992

Validation Loss
tensor(0.3626)

0.5020595192909241, [1,   101] loss: 0.3531521064515161
0.3902479410171509, [1,   201] loss: 0.3531537940772019
0.4710995852947235, [1,   301] loss: 0.35348712519256775
0.3586219847202301, [1,   401] loss: 0.35213827159710

0.48363521695137024, [1,   101] loss: 0.6387832400822403
0.45703503489494324, [1,   201] loss: 0.54978096514792
0.531856119632721, [1,   301] loss: 0.5072427269232234
0.3165278136730194, [1,   401] loss: 0.4832176187835132

Validation Loss
tensor(0.4202)

0.39411264657974243, [1,   101] loss: 0.39000249779460455
0.23775264620780945, [1,   201] loss: 0.3917608815639173
0.5303884744644165, [1,   301] loss: 0.3999163484157518
0.514236569404602, [1,   401] loss: 0.4010296330747759

Validation Loss
tensor(0.4048)

0.3576374650001526, [1,   101] loss: 0.395564003598572
0.4462149739265442, [1,   201] loss: 0.39170012074471705
0.3398491442203522, [1,   301] loss: 0.3887048773343777
0.44829314947128296, [1,   401] loss: 0.38739711263604887

Validation Loss
tensor(0.3605)

0.44159018993377686, [1,   101] loss: 0.37265591013549576
0.37491267919540405, [1,   201] loss: 0.36798837151730535
0.46127480268478394, [1,   301] loss: 0.36517397104530436
0.3958005905151367, [1,   401] loss: 0.3674877325207

0.4120394289493561, [1,   101] loss: 0.6399083243738307
0.5141484141349792, [1,   201] loss: 0.5471677717136506
0.5122443437576294, [1,   301] loss: 0.5156575401261003
0.4971284568309784, [1,   401] loss: 0.4958637336320116

Validation Loss
tensor(0.4854)

0.40293923020362854, [1,   101] loss: 0.4335987321516075
0.40314701199531555, [1,   201] loss: 0.43046221833917037
0.3679600954055786, [1,   301] loss: 0.4234496991697736
0.45690232515335083, [1,   401] loss: 0.42323120157617583

Validation Loss
tensor(0.4931)

0.4953867793083191, [1,   101] loss: 0.4171262575258123
0.41652587056159973, [1,   201] loss: 0.41868997887888953
0.4283970892429352, [1,   301] loss: 0.41864071321051777
0.37347111105918884, [1,   401] loss: 0.41576880023366497

Validation Loss
tensor(0.5026)

0.33541470766067505, [1,   101] loss: 0.41578348128512355
0.23557227849960327, [1,   201] loss: 0.4118033121177806
0.49343833327293396, [1,   301] loss: 0.41283292484243844
0.3273772895336151, [1,   401] loss: 0.4107181

0.5999211668968201, [1,   101] loss: 0.6471368248509889
0.5199761986732483, [1,   201] loss: 0.5605147903534904
0.49032193422317505, [1,   301] loss: 0.528288108318351
0.4304405748844147, [1,   401] loss: 0.5065028216699115

Validation Loss
tensor(0.4623)

0.37035804986953735, [1,   101] loss: 0.4323644046441163
0.26364046335220337, [1,   201] loss: 0.4333140440099868
0.4104769825935364, [1,   301] loss: 0.4385732572736138
0.3922443985939026, [1,   401] loss: 0.4365581148803383

Validation Loss
tensor(0.4708)

0.34808388352394104, [1,   101] loss: 0.4238725019858615
0.4100380837917328, [1,   201] loss: 0.42953612970475535
0.5074146389961243, [1,   301] loss: 0.431984100181399
0.26771244406700134, [1,   401] loss: 0.4310812095454209

Validation Loss
tensor(0.4598)

0.39043018221855164, [1,   101] loss: 0.4273594457397957
0.48700347542762756, [1,   201] loss: 0.4298724689479195
0.49422040581703186, [1,   301] loss: 0.42753347448781875
0.19611121714115143, [1,   401] loss: 0.4267335575064

0.49189358949661255, [1,   101] loss: 0.6458046518930114
0.5058581233024597, [1,   201] loss: 0.555263645909912
0.5136979818344116, [1,   301] loss: 0.5182141802734711
0.27616140246391296, [1,   401] loss: 0.5021799373953717

Validation Loss
tensor(0.4707)

0.4293261468410492, [1,   101] loss: 0.43908806956640567
0.5019849538803101, [1,   201] loss: 0.43964711320934013
0.3300725221633911, [1,   301] loss: 0.43626591231537815
0.5063635110855103, [1,   401] loss: 0.43844837295890154

Validation Loss
tensor(0.4643)

0.48995447158813477, [1,   101] loss: 0.4367832954567258
0.4689652919769287, [1,   201] loss: 0.4368940582174567
0.37824320793151855, [1,   301] loss: 0.43500091261740936
0.3923392593860626, [1,   401] loss: 0.4317922355268067

Validation Loss
tensor(0.4719)

0.5122168064117432, [1,   101] loss: 0.435868502843498
0.4510487914085388, [1,   201] loss: 0.42997800403121694
0.45405030250549316, [1,   301] loss: 0.42468903797904517
0.3762251138687134, [1,   401] loss: 0.424462525457

0.5843705534934998, [1,   101] loss: 0.6469764449808857
0.5184932947158813, [1,   201] loss: 0.574613655829311

Validation Loss
tensor(0.4589)

0.5132493376731873, [1,   101] loss: 0.4566536728698428
0.4056592583656311, [1,   201] loss: 0.4594140832696981

Validation Loss
tensor(0.4492)

0.29781973361968994, [1,   101] loss: 0.4423074495084215
0.38873350620269775, [1,   201] loss: 0.4353911778820095

Validation Loss
tensor(0.4273)

0.4270138740539551, [1,   101] loss: 0.4094403285053697
0.4335569441318512, [1,   201] loss: 0.402399373958953

Validation Loss
tensor(0.4100)

0.3539080023765564, [1,   101] loss: 0.38786397431746567
0.2556006908416748, [1,   201] loss: 0.38782368563300934

Validation Loss
tensor(0.4063)

0.36925047636032104, [1,   101] loss: 0.37887163976631544
0.32871973514556885, [1,   201] loss: 0.3842039980846851

Validation Loss
tensor(0.4060)

0.46029096841812134, [1,   101] loss: 0.3782896021805187
0.33141374588012695, [1,   201] loss: 0.37503521581787375

Validatio

0.5920979380607605, [1,   101] loss: 0.6514456242617994
0.346943736076355, [1,   201] loss: 0.5666257412872504

Validation Loss
tensor(0.4561)

0.5282970070838928, [1,   101] loss: 0.45192764802734453
0.37342414259910583, [1,   201] loss: 0.4442196089533431

Validation Loss
tensor(0.4435)

0.32925403118133545, [1,   101] loss: 0.43565006391836864
0.5204739570617676, [1,   201] loss: 0.43278038805693536

Validation Loss
tensor(0.4390)

0.3189048767089844, [1,   101] loss: 0.4270792988562348
0.3596217632293701, [1,   201] loss: 0.42947233746300884

Validation Loss
tensor(0.4370)

0.38886773586273193, [1,   101] loss: 0.41929672997776823
0.491831511259079, [1,   201] loss: 0.42431315282980603

Validation Loss
tensor(0.4315)

0.5356016755104065, [1,   101] loss: 0.4207868911694772
0.44204506278038025, [1,   201] loss: 0.4115363344253592

Validation Loss
tensor(0.4125)

0.4453839659690857, [1,   101] loss: 0.39051104086165384
0.48227250576019287, [1,   201] loss: 0.3969313583489674

Validat

In [ ]:
#@title Train LSTM

# To save or load a model with a particular name (e.g. FINAL_fnn_7gram_15hidden_5layers_bce_loss_20epochs),
# specify the name below. Otherwise, set model_name to None.
model_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Models/Uniform/Family'
preds_folder = '/content/drive/MyDrive/CompLing Projects/Voynich/Final/Predictions/Uniform/Family'

for family in families:
  for lang in family[1]:
    # Set random seeds
    random.seed(seed)
    np.random.seed(seed)
    torch.use_deterministic_algorithms(True if device.type=='cpu' else False)
    torch.manual_seed(seed)

    # Set Datasets
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Train_Uniform.pickle'), 'rb') as f:
      family_train_ds = pickle.load(f)
    with open(os.path.join(data_folder, 'Uniform', 'Family', f'{family[0]}_{lang[1]}_Val_Uniform.pickle'), 'rb') as f:
      family_val_ds = pickle.load(f)

    # Set samplers and DataLoaders
    train_sampler = EqualLengthsBatchSampler(family_train_ds, batch_size, seed)
    train_dl = DataLoader(family_train_ds, batch_sampler=train_sampler)
    val_sampler = EqualLengthsBatchSampler(family_val_ds, batch_size, seed)
    val_dl = DataLoader(family_val_ds, batch_sampler=val_sampler)

    # Set up model
    model_name = f'{family[0]}_{lang[1]}_LSTM_Uniform'
    family_lstm_model = NgramLSTM(hidden_size=15, n_layers=10, bidirectional=True).to(device)

    # Train model and log on wandb
    family_lstm_model.fit_wandb(train_dl, val_dl, epochs=10, loss_fn='bce', run_name=model_name, lstm=True)

    # Save model to Drive
    torch.save(family_lstm_model.state_dict(), os.path.join(model_folder, f'{model_name}.pt'))

    # Run predictions on Test Dataloader
    test_dl = DataLoader(test_ds, batch_size=1, shuffle=False)
    preds, sylls = family_lstm_model.predict(test_dl, separate_words=True, lstm=True)

    # Format predictions, ground truths, languages, word indices, positions, and segments
    # to feed into Pandas DataFrame
    new_preds = [entry for row in preds for entry in row.cpu().numpy()]
    new_sylls = [entry for row in sylls for entry in row.cpu().numpy()]
    sylls_check = [entry for row in test_ds for entry in row[1]]
    new_langs = [entry[2] for entry in test_ds for i in range(len(entry[1]))]
    new_ids = [id for id in range(len(test_ds)) for j in range(len(test_ds[id][1]))]
    new_positions = [i for entry in test_ds for i in range(len(entry[1]))]
    new_segments = [segment for entry in test_ds for segment in entry[3]]
    for i in range(len(sylls_check)):
      assert (new_sylls[i] == sylls_check[i]).all(), f'Check syllables at {i}.'

    family_lstm_output = pd.DataFrame({'Predictions':new_preds, 'Ground Truths':sylls_check, 'Languages':new_langs, 'Word Indices':new_ids,
                              'Positions':new_positions, 'Segments':new_segments})

    family_lstm_output.to_csv(os.path.join(preds_folder, f'{model_name}.csv'), index=False)

0.5647227764129639, [1,   101] loss: 0.6312057187061498
0.4925318956375122, [1,   201] loss: 0.5750824827608184
0.463221937417984, [1,   301] loss: 0.5317042200668309
0.307621031999588, [1,   401] loss: 0.5017265270550055

Validation Loss
tensor(0.4498)

0.4330886900424957, [1,   101] loss: 0.39984682471592825
0.47157296538352966, [1,   201] loss: 0.39739612213785375
0.42976298928260803, [1,   301] loss: 0.4018412490446504
0.39031165838241577, [1,   401] loss: 0.39820917300935693

Validation Loss
tensor(0.4381)

0.4003787636756897, [1,   101] loss: 0.39390990529024955
0.3431183993816376, [1,   201] loss: 0.38513532922190813
0.2912004888057709, [1,   301] loss: 0.3928679570654698
0.4256138801574707, [1,   401] loss: 0.389984646211715

Validation Loss
tensor(0.4380)

0.394631028175354, [1,   101] loss: 0.39144346826147325
0.4662773311138153, [1,   201] loss: 0.3938202127925496
0.21401314437389374, [1,   301] loss: 0.3862892122710266
0.4493325352668762, [1,   401] loss: 0.3868843146467446

0.5999917984008789, [1,   101] loss: 0.6324409190380927
0.481553852558136, [1,   201] loss: 0.5861348315554472
0.5003456473350525, [1,   301] loss: 0.5492172164972439
0.41398340463638306, [1,   401] loss: 0.5189805932138626

Validation Loss
tensor(0.3895)

0.3052092492580414, [1,   101] loss: 0.43106525627398257
0.5180770754814148, [1,   201] loss: 0.43093814964021615
0.40143144130706787, [1,   301] loss: 0.4299962496341661
0.4572449028491974, [1,   401] loss: 0.4268798515237775

Validation Loss
tensor(0.3773)

0.4985203742980957, [1,   101] loss: 0.42893329845501643
0.35661250352859497, [1,   201] loss: 0.426405071211395
0.4466085433959961, [1,   301] loss: 0.4218541041412623
0.44019657373428345, [1,   401] loss: 0.4218766769751944

Validation Loss
tensor(0.3764)

0.5500427484512329, [1,   101] loss: 0.41613852638419313
0.46683645248413086, [1,   201] loss: 0.41746785006119835
0.5449549555778503, [1,   301] loss: 0.4169774858212946
0.413954496383667, [1,   401] loss: 0.416838462996363

0.5391969084739685, [1,   101] loss: 0.6293091408096918
0.5017036199569702, [1,   201] loss: 0.5744425022780005
0.5374782681465149, [1,   301] loss: 0.5323591753840446
0.31633076071739197, [1,   401] loss: 0.5049073189459834

Validation Loss
tensor(0.4261)

0.41413620114326477, [1,   101] loss: 0.3983764703025912
0.2700675427913666, [1,   201] loss: 0.4030253309663849
0.5416862368583679, [1,   301] loss: 0.41268958542434087
0.5243115425109863, [1,   401] loss: 0.4131831145215956

Validation Loss
tensor(0.4179)

0.35512202978134155, [1,   101] loss: 0.40639345370011754
0.46343040466308594, [1,   201] loss: 0.4053583060627553
0.35513836145401, [1,   301] loss: 0.40468607675841084
0.4892043173313141, [1,   401] loss: 0.4063404447810162

Validation Loss
tensor(0.4095)

0.48558345437049866, [1,   101] loss: 0.4046817575719687
0.4034439027309418, [1,   201] loss: 0.40012101123146526
0.4969860911369324, [1,   301] loss: 0.39756925279225075
0.47090667486190796, [1,   401] loss: 0.4008722564779

0.5545254349708557, [1,   101] loss: 0.6516624376325324
0.5238143801689148, [1,   201] loss: 0.5855990371004266
0.5290183424949646, [1,   301] loss: 0.5453520786524612
0.5316870808601379, [1,   401] loss: 0.5212656129476733

Validation Loss
tensor(0.4873)

0.4142744839191437, [1,   101] loss: 0.45260154492784255
0.3923276364803314, [1,   201] loss: 0.45115437102851585
0.41193079948425293, [1,   301] loss: 0.4442552131572831
0.4966382086277008, [1,   401] loss: 0.4441077698793197

Validation Loss
tensor(0.4803)

0.5197468400001526, [1,   101] loss: 0.4397647785078181
0.4671107530593872, [1,   201] loss: 0.44365161983527945
0.4543197453022003, [1,   301] loss: 0.4428116157898475
0.3973419666290283, [1,   401] loss: 0.43954570190121706

Validation Loss
tensor(0.4878)

0.3658572733402252, [1,   101] loss: 0.4361379308865802
0.2466241866350174, [1,   201] loss: 0.4328439756857222
0.5089029669761658, [1,   301] loss: 0.43418616922788844
0.36161476373672485, [1,   401] loss: 0.431558443683935

0.6103647351264954, [1,   101] loss: 0.6388425732603168
0.5376548767089844, [1,   201] loss: 0.5759020468488855
0.49536454677581787, [1,   301] loss: 0.542844838428735
0.43966028094291687, [1,   401] loss: 0.520077670304258

Validation Loss
tensor(0.4704)

0.378426730632782, [1,   101] loss: 0.4482927210260146
0.26849713921546936, [1,   201] loss: 0.44936051612617955
0.42886415123939514, [1,   301] loss: 0.45583062074410163
0.42063257098197937, [1,   401] loss: 0.4550415125682467

Validation Loss
tensor(0.4620)

0.3591052293777466, [1,   101] loss: 0.4433042311137266
0.43035730719566345, [1,   201] loss: 0.4491570935542904
0.516277015209198, [1,   301] loss: 0.45175791318927494
0.2659803628921509, [1,   401] loss: 0.45063322059754424

Validation Loss
tensor(0.4622)

0.42331957817077637, [1,   101] loss: 0.44886238904817416
0.5054784417152405, [1,   201] loss: 0.45006832311078165
0.4995368421077728, [1,   301] loss: 0.4466506217581613
0.2077307105064392, [1,   401] loss: 0.4460153691993

0.5767638683319092, [1,   101] loss: 0.6427699528118171
0.5376040935516357, [1,   201] loss: 0.5810021637980618
0.5082612633705139, [1,   301] loss: 0.5387021265552685
0.2794325649738312, [1,   401] loss: 0.5188682320483605

Validation Loss
tensor(0.4683)

0.4407280385494232, [1,   101] loss: 0.4468888373363136
0.5060887336730957, [1,   201] loss: 0.4463084512089022
0.3286711275577545, [1,   301] loss: 0.4422119983109921
0.5188421010971069, [1,   401] loss: 0.4435821436717177

Validation Loss
tensor(0.4705)

0.5022091865539551, [1,   101] loss: 0.44284658119229986
0.47642385959625244, [1,   201] loss: 0.4423461717307864
0.3780762553215027, [1,   301] loss: 0.44131507051248486
0.3903239965438843, [1,   401] loss: 0.4387376245826557

Validation Loss
tensor(0.4723)

0.5114472508430481, [1,   101] loss: 0.4481914196864213
0.46360981464385986, [1,   201] loss: 0.4409751711941477
0.4592200815677643, [1,   301] loss: 0.4357588045373311
0.3903789818286896, [1,   401] loss: 0.43654665352772004


0.5896157622337341, [1,   101] loss: 0.6355191728856304
0.5543055534362793, [1,   201] loss: 0.5884676795100692

Validation Loss
tensor(0.4909)

0.527817964553833, [1,   101] loss: 0.47926845158090686
0.41095149517059326, [1,   201] loss: 0.473886722504203

Validation Loss
tensor(0.4519)

0.3176456689834595, [1,   101] loss: 0.4544980239012454
0.4306684732437134, [1,   201] loss: 0.45127574784393926

Validation Loss
tensor(0.4444)

0.48212161660194397, [1,   101] loss: 0.45018728409368214
0.49077120423316956, [1,   201] loss: 0.44551282616990123

Validation Loss
tensor(0.4431)

0.3986646234989166, [1,   101] loss: 0.4414853697070981
0.28311318159103394, [1,   201] loss: 0.443598500809711

Validation Loss
tensor(0.4422)

0.4207094609737396, [1,   101] loss: 0.4347217966719429
0.39450255036354065, [1,   201] loss: 0.44542200574234353

Validation Loss
tensor(0.4396)

0.540848970413208, [1,   101] loss: 0.443576779843557
0.413630872964859, [1,   201] loss: 0.4407174988320811

Validation Lo

0.5959298014640808, [1,   101] loss: 0.6325872696862362
0.4131452739238739, [1,   201] loss: 0.5803822731200735

Validation Loss
tensor(0.4878)

0.5337175130844116, [1,   101] loss: 0.47248833574871024
0.3977239727973938, [1,   201] loss: 0.46014794529373965

Validation Loss
tensor(0.4620)

0.35459190607070923, [1,   101] loss: 0.44896032594808255
0.5311381220817566, [1,   201] loss: 0.44515521060768054

Validation Loss
tensor(0.4509)

0.3292495608329773, [1,   101] loss: 0.4376614061322543
0.37952589988708496, [1,   201] loss: 0.4399665976267549

Validation Loss
tensor(0.4452)

0.38232266902923584, [1,   101] loss: 0.43038456119818264
0.505006730556488, [1,   201] loss: 0.43842382402858926

Validation Loss
tensor(0.4448)

0.5518094897270203, [1,   101] loss: 0.4419203017017629
0.5090464949607849, [1,   201] loss: 0.43714808583704395

Validation Loss
tensor(0.4436)

0.4844544231891632, [1,   101] loss: 0.420909581207993
0.5445120334625244, [1,   201] loss: 0.43292855098843575

Validati